In [34]:
%load_ext autoreload
%autoreload 2

In [35]:
"""
Author: Ashyam Zubair
Created Date: 14-02-2019
"""
import json
import pandas as pd
import traceback
import sqlalchemy
import os

from MySQLdb._exceptions import OperationalError
from sqlalchemy import create_engine, exc
from time import time

# try:
#     from app.ace_logger import Logging
# except:
#     from ace_logger import Logging
     
# logging = Logging()

import logging
class DB(object):
    def __init__(self, database, host='127.0.0.1', user='root', password='', port='3306', tenant_id=None):
        """
        Initialization of databse object.

        Args:
            databse (str): The database to connect to.
            host (str): Host IP address. For dockerized app, it is the name of
                the service set in the compose file.
            user (str): Username of MySQL server. (default = 'root')
            password (str): Password of MySQL server. For dockerized app, the
                password is set in the compose file. (default = '')
            port (str): Port number for MySQL. For dockerized app, the port that
                is mapped in the compose file. (default = '3306')
        """

        if host in ["common_db","extraction_db", "queue_db", "template_db", "table_db", "stats_db", "business_rules_db", "reports_db"]:
            self.HOST = os.environ['HOST_IP']
            self.USER = 'root'
            self.PASSWORD = os.environ['LOCAL_DB_PASSWORD']
            self.PORT = '3306'
            self.DATABASE = f'{tenant_id}_{database}' if tenant_id is not None and tenant_id else database
        else:
            self.HOST = host
            self.USER = user
            self.PASSWORD = password
            self.PORT = port
            self.DATABASE = f'{tenant_id}_{database}' if tenant_id is not None and tenant_id else database
        
        logging.info(f'Host: {self.HOST}')
        logging.info(f'User: {self.USER}')
        logging.info(f'Password: {self.PASSWORD}')
        logging.info(f'Port: {self.PORT}')
        logging.info(f'Database: {self.DATABASE}')

        self.connect()

    def connect(self, max_retry=5):
        retry = 1

        try:
            start = time.time()
            logging.debug(f'Making connection to `{self.DATABASE}`...')
            config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{self.DATABASE}?charset=utf8'
            self.db_ = create_engine(config, connect_args={'connect_timeout': 2}, pool_recycle=300)
            logging.info(f'Engine created for `{self.DATABASE}`')
            while retry <= max_retry:
                try:
                    self.engine = self.db_.connect()
                    logging.info(f'Connection established succesfully to `{self.DATABASE}`! ({round(time.time() - start, 2)} secs to connect)')
                    break
                except Exception as e:
                    logging.warning(f'Connection failed. Retrying... ({retry}) [{e}]')
                    retry += 1
                    self.db_.dispose()
        except:
            logging.exception(f'Something went wrong while connecting. Check trace.')
            return

    def execute(self, query, database=None, **kwargs):
        """
        Executes an SQL query.

        Args:
            query (str): The query that needs to be executed.
            database (str): Name of the database to execute the query in. Leave
                it none if you want use database during object creation.
            params (list/tuple/dict): List of parameters to pass to in the query.

        Returns:
            (DataFrame) A pandas dataframe containing the data from the executed
            query. (None if an error occurs)
        """
        data = None

        # Use new database if a new databse is given
        if database is not None:
            try:
                config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{database}?charset=utf8'
                engine = create_engine(config, pool_recycle=300)
            except:
                logging.exception(f'Something went wrong while connecting. Check trace.')
                return False
        else:
            engine = self.engine

        try:
            logging.debug(f'Query: {query}')
            data = pd.read_sql(query, engine, index_col='id', **kwargs)
        except exc.ResourceClosedError:
            logging.warning('Query does not have any value to return.')
            return True
        except (exc.StatementError, OperationalError) as e:
            logging.warning(f'Creating new connection. Engine/Connection is probably None. [{e}]')
            self.connect()
            data = pd.read_sql(query, self.engine, index_col='id', **kwargs)
        except:
            logging.exception('Something went wrong executing query. Check trace.')
            params = kwargs['params'] if 'params' in kwargs else None
            return False

        return data.where((pd.notnull(data)), None)

    def execute_(self, query, database=None, **kwargs):
        """
        Executes an SQL query.

        Args:
            query (str): The query that needs to be executed.
            database (str): Name of the database to execute the query in. Leave
                it none if you want use database during object creation.
            params (list/tuple/dict): List of parameters to pass to in the query.

        Returns:
            (DataFrame) A pandas dataframe containing the data from the executed
            query. (None if an error occurs)
        """
        data = None

        # Use new database if a new databse is given
        if database is not None:
            try:
                config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{database}?charset=utf8'
                engine = create_engine(config, pool_recycle=300)
            except:
                logging.exception(f'Something went wrong while connecting. Check trace.')
                return False
        else:
            engine = self.engine

        try:
            data = pd.read_sql(query, engine, **kwargs)
        except exc.ResourceClosedError:
            return True
        except:
            logging.exception(f'Something went wrong while connecting. Check trace.')
            params = kwargs['params'] if 'params' in kwargs else None
            return False

        return data.replace({pd.np.nan: None})


    def insert(self, data, table, database=None, **kwargs):
        """
        Write records stored in a DataFrame to a SQL database.

        Args:
            data (DataFrame): The DataFrame that needs to be write to SQL database.
            table (str): The table in which the rcords should be written to.
            database (str): The database the table lies in. Leave it none if you
                want use database during object creation.
            kwargs: Keyword arguments for pandas to_sql function.
                See https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.to_sql.html
                to know the arguments that can be passed.

        Returns:
            (bool) True is succesfully inserted, else false.
        """
        logging.info(f'Inserting into `{table}`')

        # Use new database if a new databse is given
        if database is not None:
            try:
                config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{database}?charset=utf8'
                engine = create_engine(config, pool_recycle=300)
            except:
                logging.exception(f'Something went wrong while connecting. Check trace.')
                return False
        else:
            engine = self.engine

        try:
            data.to_sql(table, engine, **kwargs)
            try:
                self.execute(f'ALTER TABLE `{table}` ADD PRIMARY KEY (`id`);')
            except:
                pass
            return True
        except:
            logging.exception('Something went wrong inserting. Check trace.')
            return False

    def insert_dict(self, data, table):
        """
        Insert dictionary into a SQL database table.

        Args:
            data (DataFrame): The DataFrame that needs to be write to SQL database.
            table (str): The table in which the rcords should be written to.

        Returns:
            (bool) True is succesfully inserted, else false.
        """
        logging.info(f'Inserting dictionary data into `{table}`...')
        logging.debug(f'Data:\n{data}')

        try:
            column_names = []
            params = []

            for column_name, value in data.items():
                column_names.append(f'`{column_name}`')
                params.append(value)

            logging.debug(f'Column names: {column_names}')
            logging.debug(f'Params: {params}')

            columns_string = ', '.join(column_names)
            param_placeholders = ', '.join(['%s'] * len(column_names))

            query = f'INSERT INTO {table} ({columns_string}) VALUES ({param_placeholders})'

            return self.execute(query, params=params)
        except:
            logging.exception('Error inserting data.')
            return False

    def update(self, table, update=None, where=None, database=None, force_update=False):
        # Use new database if a new databse is given
        if database is not None:
            try:
                config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{database}?charset=utf8'
                self.engine = create_engine(config, pool_recycle=300)
            except:
                logging.exception(f'Something went wrong while connecting. Check trace.')
                return False

        logging.info(f'Updating table: `{table}`')
        logging.info(f'Update data: `{update}`')
        logging.info(f'Where clause data: `{where}`')
        logging.info(f'Force update flag: `{force_update}`')

        try:
            set_clause = []
            set_value_list = []
            where_clause = []
            where_value_list = []

            if where is not None and where:
                for set_column, set_value in update.items():
                    set_clause.append(f'`{set_column}`=%s')
                    set_value_list.append(set_value)
                set_clause_string = ', '.join(set_clause)
            else:
                logging.error(f'Update dictionary is None/empty. Must have some update clause.')
                return False

            if where is not None and where:
                for where_column, where_value in where.items():
                    where_clause.append(f'{where_column}=%s')
                    where_value_list.append(where_value)
                where_clause_string = ' AND '.join(where_clause)
                query = f'UPDATE `{table}` SET {set_clause_string} WHERE {where_clause_string}'
            else:
                if force_update:
                    query = f'UPDATE `{table}` SET {set_clause_string}'
                else:
                    message = 'Where dictionary is None/empty. If you want to force update every row, pass force_update as True.'
                    logging.error(message)
                    return False

            params = set_value_list + where_value_list
            self.execute(query, params=params)
            return True
        except:
            logging.exception('Something went wrong updating. Check trace.')
            return False

    def get_column_names(self, table, database=None):
        """
        Get all column names from an SQL table.

        Args:
            table (str): Name of the table from which column names should be extracted.
            database (str): Name of the database in which the table lies. Leave
                it none if you want use database during object creation.

        Returns:
            (list) List of headers. (None if an error occurs)
        """
        try:
            logging.info(f'Getting column names of table `{table}`')
            return list(self.execute(f'SELECT * FROM `{table}`', database))
        except:
            logging.exception('Something went wrong getting column names. Check trace.')
            return

    def execute_default_index(self, query, database=None, **kwargs):
        """
        Executes an SQL query.

        Args:
            query (str): The query that needs to be executed.
            database (str): Name of the database to execute the query in. Leave
                it none if you want use database during object creation.
            params (list/tuple/dict): List of parameters to pass to in the query.

        Returns:
            (DataFrame) A pandas dataframe containing the data from the executed
            query. (None if an error occurs)
        """
        data = None

        # Use new database if a new databse is given
        if database is not None:
            try:
                config = f'mysql://{self.USER}:{self.PASSWORD}@{self.HOST}:{self.PORT}/{database}?charset=utf8'
                engine = create_engine(config, pool_recycle=300)
            except:
                logging.exception(f'Something went wrong while connecting. Check trace.')
                return False
        else:
            engine = self.engine

        try:
            data = pd.read_sql(query, engine, **kwargs)
        except exc.ResourceClosedError:
            return True
        except:
            logging.exception(f'Something went wrong while executing query. Check trace.')
            params = kwargs['params'] if 'params' in kwargs else None
            return False

        return data.where((pd.notnull(data)), None)


    def get_all(self, table, database=None, discard=None):
        """
        Get all data from an SQL table.

        Args:
            table (str): Name of the table from which data should be extracted.
            database (str): Name of the database in which the table lies. Leave
                it none if you want use database during object creation.
            discard (list): columns to be excluded while selecting all
        Returns:
            (DataFrame) A pandas dataframe containing the data. (None if an error
            occurs)
        """
        logging.info(f'Getting all data from `{table}`')
        if discard:
            logging.info(f'Discarding columns `{discard}`')
            columns = list(self.execute_default_index(f'SHOW COLUMNS FROM `{table}`',database).Field)
            columns = [col for col in columns if col not in discard]
            columns_str = json.dumps(columns).replace("'",'`').replace('"','`')[1:-1]
            return self.execute(f'SELECT {columns_str} FROM `{table}`', database)

        return self.execute(f'SELECT * FROM `{table}`', database)

    def get_latest(self, data, group_by_col, sort_col):
        """
        Group data by a column containing repeated values and get latest from it by
        taking the latest value based on another column.

        Example:
        Get the latest products
            id     product   date
            220    6647     2014-09-01
            220    6647     2014-10-16
            826    3380     2014-11-11
            826    3380     2015-05-19
            901    4555     2014-09-01
            901    4555     2014-11-01

        The function will return
            id     product   date
            220    6647     2014-10-16
            826    3380     2015-05-19
            901    4555     2014-11-01

        Args:
            data (DataFrame): Pandas DataFrame to query on.
            group_by_col (str): Column containing repeated values.
            sort_col (str): Column to identify the latest record.

        Returns:
            (DataFrame) Contains the latest records. (None if an error occurs)
        """
        try:
            logging.info('Grouping data...')
            logging.info(f'Data: {data}')
            logging.info(f'Group by column: {group_by_col}')
            logging.info(f'Sort column: {sort_col}')
            return data.sort_values(sort_col).groupby(group_by_col).tail(1)
        except KeyError as e:
            logging.errot(f'Column `{e.args[0]}` does not exist.')
            return None
        except:
            logging.exception('Something went wrong while grouping data.')
            return None


In [37]:
import os
os.environ['HOST_IP'] = '3.208.195.34'
os.environ['HOST_IP'] = '52.90.56.244'
os.environ['LOCAL_DB_USER'] = 'root'
os.environ['LOCAL_DB_PASSWORD'] = 'AlgoTeam123'
os.environ['LOCAL_DB_PORT'] = '3306'

tenant_id = 'karvy'

db_config = {
    'host': os.environ['HOST_IP'],
    'user': os.environ['LOCAL_DB_USER'],
    'password': os.environ['LOCAL_DB_PASSWORD'],
    'port': os.environ['LOCAL_DB_PORT']
}

In [38]:
# %load apply_business_rule.py
try:
    # comment below two for local testing
    from ace_logger import Logging
    logging = Logging()  
    from db_utils import DB 
      
except Exception as e:
    # uncomment these below lines for local testing
    import logging 
    logger=logging.getLogger() 
    logger.setLevel(logging.DEBUG) 

import time,datetime
import pandas as pd
import ntpath
import numpy as np
import re

import pandas as pd
from pyxlsb import open_workbook as open_xlsb

import json
import os
import re


from BusinessRules import BusinessRules

# one configuration
db_config = {
    'host': os.environ['HOST_IP'],
    'user': os.environ['LOCAL_DB_USER'],
    'password': os.environ['LOCAL_DB_PASSWORD'],
    'port': os.environ['LOCAL_DB_PORT']
}


# give any path...platform independent...get the base name
def path_leaf(path):
    """give any path...platform independent...get the base name"""
    head, tail = ntpath.split(path)
    return tail or ntpath.basename(head)


def to_DT_data(parameters):
    """Amith's processing for parameters"""
    output = []
    try:
        for param_dict in parameters:
            print(param_dict)    
            if param_dict['column'] == 'Add_on_Table':
                output.append({'table': param_dict['table'],'column': param_dict['column'],'value': param_dict['value']})
                # Need to add a function to show this or tell Kamal check if its addon table and parse accordingly
            else:                
                output.append({'table': param_dict['table'],'column': param_dict['column'],'value': param_dict['value']})
    except:
        print("Error in to_DT_data()")
        traceback.print_exc()
        return []
    try:
        output = [dict(t) for t in {tuple(d.items()) for d in output}]
    except:
        print("Error in removing duplicate dictionaries in list")
        traceback.print_exc()
        pass
    return output

def get_data_sources(tenant_id, case_id, column_name, master=False):
    """Helper to get all the required table data for the businesss rules to apply
    """
    get_datasources_query = "SELECT * from `data_sources`"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    data_sources = business_rules_db.execute(get_datasources_query)


    # sources
    sources = json.loads(list(data_sources[column_name])[0])
    
    
    data = {}
    for database, tables in sources.items():
        db = DB(database, tenant_id=tenant_id, **db_config)
        for table in tables:
            if master:
                query = f"SELECT * from `{table}`"
                df = db.execute(query)
            else:
                query = f"SELECT * from `{table}` WHERE case_id = %s"
                params = [case_id]
                df = db.execute(query, params=params)
            if not df.empty:
                data[table] = df.to_dict(orient='records')[0]
            else:
                data[table] = {}
    
    
    case_id_based_sources = json.loads(list(data_sources['case_id_based'])[0])
    
    return data
                
def get_rules(tenant_id, group):
    """Get the rules based on the stage, tenant_id"""
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    get_rules_query = "SELECT * from `sequence_rule_data` where `group` = %s"
    params = [group]
    rules = business_rules_db.execute(get_rules_query, params=params)
    return rules

def update_tables(case_id, tenant_id, updates):
    """Update the values in the database"""
    try:
        extraction_db = DB('extraction', tenant_id=tenant_id, **db_config) # only in ocr or process_queue we are updating
        queue_db = DB('queues', tenant_id=tenant_id, **db_config) # only in ocr or process_queue we are updating
        
        for table, colum_values in updates.items():
            if table == 'ocr':
                extraction_db.update(table, update=colum_values, where={'case_id':case_id})
            if table == 'process_queue':
                queue_db.update(table, update=colum_values, where={'case_id':case_id})
    except Exception as e:
        logging.error("Error in updating the tables")
        logging.error("check whether the table exists")
        logging.error(e)
        
    return "UPDATED IN THE DATABASE SUCCESSFULLY"

def capture_matrix(df,file_name, tenant_id):
    total_count = len(df.index)
    rejected_count = len(df[df['Filter'] == 'Y'])
    query = f"INSERT INTO `capture_matrix`(`file_name`, `total_count`, `rejected_count`) VALUES ('{file_name}',{total_count},{rejected_count})"
    try:
        db = DB('business_rules', tenant_id=tenant_id, **db_config)
        db.execute(query,'karvy_business_rules')
    except Exception as e:
        logging.error("Error in updating the table of capture_matrix")
        logging.error("check whether the table exists")
        logging.error(e)

    return "UPDATED CAPTURE MATRIX IN THE DATABASE SUCCESSFULLY"

def get_account_no(df):
    for ele in list(df.columns):
        if  ('Account No' in str(ele) or 'Account Number' in str(ele)):
            for e in list(df.columns):
                accnos = (re.findall('[0-9]{9,18}', str(e)))
                if accnos:
                    return accnos[0]
            break

    for index, row in df.iterrows():
        #print(f"index {index}, rows {row}")
        for ele in list(row):
            #print(f"ele is {ele}")
            if  ('Account No' in str(ele) or 'Account No.' in str(ele) or 'Account Number' in str(ele) or 'Account Id' in str(ele) or 'Transactions List' in str(ele)):
                for e in row:
                    accnos = (re.findall('[0-9]{9,18}', str(e)))
                    if accnos:
                        return accnos[0]
                break
    return 'column'

def get_new_df(df,stage, tenant_id):
    
    header_map_query = "SELECT `headers` FROM `bank_headers_mapping` where BANK=%s"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    df = df.dropna(axis = 1,how='all')

    headers_df = business_rules_db.execute_default_index(header_map_query, params=[stage])
    
    if not headers_df.empty:
        headers = json.loads(headers_df['headers'][0])
        print (headers)
        for index, row in df.iterrows():
            key = stage
            values = headers
            strips_rows = [str(ele).strip() for ele in list(row)]
            strip_values = [str(ele).strip() for ele in values]
            if (strips_rows[0] == strip_values[0] and strips_rows[1] == strip_values[1]):

                new_header = df.iloc[index] #grab the first row for the header
                df = df[index+1:] #take the data less the header row
                df.columns = new_header #set the header row as the df header
                return df
    
    return df


def generate_feed_sub_feed_bank(df, account_number, stage, tenant_id):
    
    
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    query = "SELECT * FROM `bank_key_subfeed`"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    query = "SELECT * FROM `bank_key_subfeed`"
    key_subfeed_map = json.loads(business_rules_db.execute_default_index(query)['key_subfeed_value'][0])

    def get_sub_feed(row):
        for key,sub_feed in key_subfeed_map.items():
            # print('key ',key, 'subfeed ',sub_feed)
            # print(row['Transaction Description'])
            if str(key).lower() in str(row['Transaction Description']).lower():
                row['Sub_Feed'] = sub_feed
                return row
        row['Filter'] = 'N'
        return row

    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    feed_sub_df = business_rules_db.execute_default_index("SELECT * FROM `bank_feed_details` WHERE `account`=%s", params=[account_number])
    print ("Feed subfeed df")
    print (feed_sub_df)
    feed = feed_sub_df['feed'][0]
    df['Feed'] = feed 
    
    sub_feed = feed_sub_df['sub_feed'][0]
    if sub_feed:
        print ("SUB FEED GOT FROM BANK", sub_feed)
        df['Sub_Feed'] = sub_feed
    else:
        df['Sub_Feed'] = ''
        df = df.apply(get_sub_feed, axis=1)
    
    return df


def generate_feed_id(df, stage, tenant_id, type_="Feed"):
    
    if type_ == "Feed":
        df['Feed_ID'] = ''
    else:
        df['Bank_ID'] = ''
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    DF= business_rules_db.execute_default_index("SELECT `row_count` from `standard_column_mapping` where feed_subfeed=%s", params=[stage])
    
    if type_ == 'Feed':
        df['Feed_ID'] = df['Feed']+"_"+df['Sub_Feed']+"_"+(df.index + list(DF['row_count'])[0]).astype(str)
    else:
        df['Bank_ID'] = stage +"_"+(df.index + list(DF['row_count'])[0]).astype(str)

    business_rules_db.execute_default_index("UPDATE `standard_column_mapping` SET `row_count`= %s WHERE feed_subfeed=%s",params=[len(df)+list(DF['row_count'])[0], stage])

    return df

def strip_date_time(df, column, new_column_date, new_column_time):
    df[column] = pd.to_datetime(df[column], dayfirst=True, errors='coerce')
    df[new_column_date] = df[column].dt.date
    df[new_column_time] = df[column].dt.time
    return df

def consider_amount_negative(df, amount_column, credit_column, credit_val):
    df[amount_column] = df[amount_column].astype(float)
    df[amount_column] = df[amount_column].where(df[credit_column] != credit_val, df[amount_column]*-1)
    return df

def filter_rows(df, account_no, account_no_filter_map, filter_field):
    filter_values = []
    if account_no in account_no_filter_map:
        filter_values = account_no_filter_map[account_no]
    for val in filter_values:
        df['Filter'] = df['Filter'].where((df[filter_field].astype(str).str.contains(val)), 'N')
    
    return df

def writeToCsv(df, file_path_raw_, file_path, tenant_id, stage, required_raw_mapping=None, required_standard_mapping=None, type_='Feed'):
    """Write the dataframe to csv"""
    print ("required standard mapping got is")
    print (required_standard_mapping)
    
    if not required_standard_mapping:
        required_standard_mapping = {ele:ele for ele in list(df.columns)}
    
    if type_ == 'Feed':
        required_columns_raw = [ele for ele in df.columns if (ele != 'Feed' and ele!='Sub_Feed' and ele!='ID')]
        required_columns_raw = ['Feed_ID', 'Raw_Id', 'case_id'] + required_columns_raw + ['queue']
    else:
        required_columns_raw = [ele for ele in df.columns if (ele!='ID')]
        required_columns_raw = ['Bank_ID', 'Raw_Id', 'case_id'] + required_columns_raw + ['queue']
        
    df = generate_feed_id(df, stage, tenant_id, type_)
    
    # write the processed_raw_files
    headers = True
    mode = 'w'
    logging.debug(df.columns)
    logging.debug(type_)
    print(df.columns)
    # df = df.rename(columns=required_raw_mapping)
    print(df.columns)
    # required_columns_raw = list(required_raw_mapping.values())
    if type_ == 'Feed':
        df['Raw_Id'] = df['Feed_ID']
        df['case_id'] = df['Feed_ID']
        # df = df.rename(columns=required_raw_mapping)
        required_columns_raw = list(required_raw_mapping.keys())
        required_columns_raw = ['Feed_ID', 'Raw_Id', 'case_id'] + required_columns_raw + ['queue']
    else:
        df['Raw_Id'] = df['Bank_ID']
        df['case_id'] = df['Bank_ID']
        # df = df.rename(columns=required_raw_mapping)
        required_columns_raw = list(required_raw_mapping.keys())
        required_columns_raw = ['Bank_ID', 'Raw_Id', 'case_id'] + required_columns_raw + ['queue']

    print(required_columns_raw)
    df.to_csv(file_path_raw_, columns=required_columns_raw,mode=mode, header=required_raw_mapping.values(), index=False)
    # df.to_csv(file_path_raw_, columns=required_columns_raw, index=False)
    
    # ideally get from database..
    standard_column_query = "SELECT `standard_columns` FROM `bank_stage_details`"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    required_columns = json.loads(business_rules_db.execute_default_index(standard_column_query)['standard_columns'][0])
    if type_ == 'Feed':
        required_columns = ['Feed_ID', 'Feed', 'Sub_Feed', 'Date', 'Code', 'Filter', 'Amount', 'ID', 'queue', 'Matched']
    else:
        required_columns = ['Bank_ID', 'Bank_Name', 'Feed', 'Sub_Feed','Date', 'Code', 'Filter', 'Amount', 'queue', 'Reference_number', 'timestamp' ,'Unmatched_Amount','matched_amount','ID']
    try:

        # first find whether any csv exists with the file_name
        existing_df = pd.read_csv(file_path)
        # df = df.rename(columns=required_standard_mapping)
        mode = 'a'
        headers = False
        if type_ == 'Feed':
            required_columns_in_orig_df = ['Feed_ID'] + list(required_standard_mapping.keys()) + ['ID', 'queue']
        else:  

            required_columns_in_orig_df =  list(required_standard_mapping.keys()) + ['ID']

        df.to_csv(file_path, columns=required_columns_in_orig_df, mode=mode, header=required_columns, index=False)
    except:
        # no sample file exists
        headers = True
        mode = 'w'
        
        # rename the columns in the dataframe to standardized columns            
        # df = df.rename(columns=required_standard_mapping)
        #df['Date'] = pd.to_datetime(df['Date'],dayfirst=True, errors='coerce')
        #df['Date'] = df['Date'].dt.date
        if type_ == 'Feed':
            required_columns_in_orig_df = ['Feed_ID'] + list(required_standard_mapping.keys()) + ['ID', 'queue']
        else:
            required_columns_in_orig_df =  list(required_standard_mapping.keys())


        df.to_csv(file_path, columns=required_columns_in_orig_df, mode=mode, header=required_columns, index=False)
                
    return "Written to csv successfully"



def code_apply(row):
    
    if row['Feed'].lower() == 'CPVIRTUAL'.lower():
        if str(row['Sub_Feed']) in ['CPVIRTUAL_LI99', 'CPVIRTUAL_IO99', 'CPVIRTUAL_AK99']:
            row['Code'] = row['Reference No.']
            return row
    return row
        

def hdfc_bank(hdfc_df, tenant_id, accno):
    hdfc_df = get_new_df(hdfc_df, 'HDFC', tenant_id)
    hdfc_df['Code'] = hdfc_df['Transaction Description']
    # hdfc_df['Filter'] = 'N'
    hdfc_df = strip_date_time(hdfc_df, 'Transaction Date', 'Transaction Date Date', 'Transaction Date Time')
    hdfc_df['Value Date'] = hdfc_df['Value Date'].astype(str)
    hdfc_df['Value Date'] = pd.to_datetime(hdfc_df['Value Date'], dayfirst=True, errors='coerce').dt.date
    hdfc_df = consider_amount_negative(hdfc_df, 'Transaction Amount', 'Debit / Credit', 'D')
    
    # hdfc_df['Transaction Description'] = hdfc_df['Transaction Description'].str.split("-").str[1]
    
    hdfc_df = hdfc_df.apply(code_apply, axis=1)
    
    account_no_filter_map = {
            "600350117285":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "57500000197162":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "57500000207581":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "600350087152":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "990620012131":["PAY-OUT","00990640000982"],
            "600350051109":["50200009635552"],
            "990610016361":["MFSS Normal Pay-out S"],
            "602090003198":["KARVY DATA MAN"],
            "57500000090687":["Mirae Asset ISIP Collection"],
            "57500000090303":["MIRAE ASSET SIP COLLECTION"]

        }
    
#     hdfc_df = generate_feed_id(hdfc_df, 'HDFC', tenant_id, type_='Bank')
    hdfc_df = filter_rows(hdfc_df, accno, account_no_filter_map, 'Transaction Description')

    return hdfc_df





    






def deutsche_bank(deut_df,tenant_id):
    deut_df = get_new_df(deut_df, 'DEUTSCHE', tenant_id)
    deut_df['VALUE DATE'] = deut_df['VALUE DATE'].astype(str)
    deut_df['VALUE DATE'] = pd.to_datetime(deut_df['VALUE DATE'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    deut_df['BOOK DATE'] = deut_df['BOOK DATE'].astype(str)
    deut_df['BOOK DATE'] = pd.to_datetime(deut_df['BOOK DATE'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    deut_df = strip_date_time(deut_df, 'CONROL DATE', 'CONROL DATE Date', 'CONROL DATE Time')

    return deut_df

def axis_bank(axis_df, tenant_id, accno):
    axis_df = get_new_df(axis_df, 'AXIS', tenant_id)
    axis_df['Filter'] = 'N'
    axis_df['Tran Date'] = axis_df['Tran Date'].astype(str)
    axis_df['Tran Date'] = pd.to_datetime(axis_df['Tran Date'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    axis_df = strip_date_time(axis_df, 'Tran Time', 'Tran Time Date', 'Tran Time Time')

    account_no_fileter_map = {
            "917020082397356":["ARN-64610"]
        }
    axis_df = filter_rows(axis_df, accno, account_no_fileter_map, 'Particulars')

    return axis_df
    



def syndi_bank(syndi_df, tenant_id, accno):
    syndi_df = dateConvertion(syndi_df, 'SYNDICATE', tenant_id)

    syndi_df['Value Date'] = syndi_df['Value Date'].astype(str)
    syndi_df['Value Date'] = pd.to_datetime(syndi_df['Value Date'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    syndi_df['Transaction Date'] = syndi_df['Transaction Date'].astype(str)
    syndi_df['Transaction Date'] = pd.to_datetime(syndi_df['Transaction Date'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    account_no_fileter_map = {
            "50001010022338":["ARMY GROUP INSURAN"]
        }
    syndi_df = filter_rows(syndi_df, accno, account_no_fileter_map, 'Description')

    return syndi_df

def sbi_bank(sbi_df, tenant_id):
    sbi_df = dateConvertion(sbi_df, 'SBI', tenant_id)
    sbi_df['Value Date'] = pd.to_datetime(sbi_df[column],  errors='coerce')
    sbi_df['Time'] = sbi_df['Value Date'].dt.time
    sbi_df['Value Date'] = pd.to_datetime(sbi_df['Value Date']).dt.strftime('%Y-%m-%d')
    
    return sbi_df


def kotak_code_apply(row):
    if row['Filter'] == 'N':
        return row
    try:
        
        if str(row['Account No']) == '09582540006664':
            row['Code'] = row['Chq / Ref number'].str.split("-").index[1]
            return row
        if str(row['Account No']) == '9312739875':
            row['Code'] = row['Description']
            return row
    except:
        return row
    
    return row
def kotak_bank(kotak_df,tenant_id):
    kotak_df = dateConvertion(kotak_df, 'KOTAK', tenant_id)
    kotak_df['Code'] = ''    
    kotak_df['Filter'] = kotak_df['Filter'].where(~kotak_df['Deposit'].isnull(), 'N')
    kotak_df['Value Date'] = pd.to_datetime(kotak_df['Value Date'],  errors='coerce')
    kotak_df['Time'] = kotak_df['Value Date'].dt.time
    kotak_df['Value Date'] = pd.to_datetime(kotak_df['Value Date']).dt.strftime('%Y-%m-%d')
    kotak_df = kotak_df.apply(kotak_code_apply, axis=1)
    
    return kotak_df
    

def idbi_code_apply(row):
    if row['Filter'] == 'N':
        return row
    try:
        
        if str(row['Account No']) == '004103000026965' or str(row['Account No']) == '4103000026965':
            row['Code'] = row['Description'].str.split("/").index[3]
            return row
    except:
        return row
    
    return row

def idbi_bank(idbi_df,tenant_id):
    idbi_df = dateConvertion(idbi_df, 'IDBI', tenant_id)
    
    idbi_df['Filter'] = idbi_df['Filter'].where(~(idbi_df['Cr/Dr'] == 'CR'), 'N')
    idbi_df['Time'] = pd.to_datetime(idbi_df['Txn Posted Time'], format= '%H:%M:%S', errors='coerce').dt.time

    idbi_df = consider_amount_negative(idbi_df, 'Transaction Amount(INR)', 'Cr/Dr', 'DR')
    
    idbi_df = idbi_df.apply(idbi_code_apply, axis=1)
    return idbi_df



def db_bank(db_df,tenant_id):
    db_df = dateConvertion(db_df, 'DB', tenant_id)
    db_df['CONTROL DATE'] = pd.to_datetime(db_df['CONTROL DATE'],  errors='coerce')
    db_df['Time'] = db_df['CONTROL DATE'].dt.time
    db_df['CONTROL DATE'] = pd.to_datetime(db_df['CONTROL DATE']).dt.strftime('%Y-%m-%d')
   
    return idbi_df


def icici_bank(icici_df,tenant_id):
    icici_df = dateConvertion(icici_df, 'DB', tenant_id)
    icici_df['Txn Posted Date'] = pd.to_datetime(icici_df['Txn Posted Date'],  errors='coerce')
    icici_df['Time'] = icici_df['Txn Posted Date'].dt.time
    icici_df['Txn Posted Date'] = pd.to_datetime(icici_df['Txn Posted Date']).dt.strftime('%Y-%m-%d')
   

    
    icici_df = consider_amount_negative(icici_df, 'Transaction Amount', 'Debit / Credit', 'DR')
    
    return icici_df



def citi_bank(citi_df, tenant_id, accno):
    citi_df = dateConvertion(citi_df, 'CITI', tenant_id)
    citi_df['Posted Time'] = pd.to_datetime(citi_df['Posted Time'],  errors='coerce')
    citi_df['Time'] = citi_df['Posted Time'].dt.time
    citi_df['Posted Time'] = pd.to_datetime(citi_df['Posted Time']).dt.strftime('%Y-%m-%d')
 
    
    account_no_fileter_map = {
            "0036498676":["MF SUBN IN MIRAE FUND"],
            "036498307":["PAYOUTS"]
        }

    #     citi_df = generate_feed_id(citi_df, 'HDFC', tenant_id, type_='Bank')
    citi_df = filter_rows(citi_df, accno, account_no_fileter_map, 'Narrative')
    return citi_df



def yes_bank(yes_df, tenant_id):
    yes_df = dateConvertion(yes_df, 'YES', tenant_id)
    yes_df['Transaction Date'] = pd.to_datetime(yes_df['Transaction Date'],  errors='coerce')
    yes_df['Time'] = yes_df['Transaction Date'].dt.time
    yes_df['Transaction Date'] = pd.to_datetime(yes_df['Transaction Date']).dt.strftime('%Y-%m-%d')
    yes_bank['Code'] = ''

    yes_bank['Code'] = np.where(yes_bank['Account No'] == '26885700000731', yes_bank['Reference No.'], '')
    yes_df = consider_amount_negative(yes_df, 'Transaction Amount', 'Debit / Credit', 'D')

    return yes_df
    

def generate_feed_sub_feed(df, stage, tenant_id):
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    default_maps = business_rules_db.execute_default_index("SELECT * FROM `default_value_mapping`")
    default_values = json.loads(default_maps['default_values'][0])
    stage_feed_maps = json.loads(default_maps['stage_feed_mapping'][0])
    
    for column, value in default_values.items():
        df[column] = value
    df['Sub_Feed'] =  stage
    df['Feed'] = stage_feed_maps[stage]
    return df

def dateConvertion(df,stage,tenant_id):
    try:
        db = DB('business_rules', tenant_id=tenant_id, **db_config)
        query = f"SELECT `date_columns` FROM `standard_column_mapping` WHERE `feed_subfeed` = '{stage}'"
        columns = db.execute_default_index(query,'karvy_business_rules')
        columns = json.loads(columns['date_columns'][0])
    except Exception as e:
        logging.error("Cannot get columns data")
        logging.error(e)
    
    for column in columns:
        df[column] = df[column].astype(str)
        df[column] =  pd.to_datetime(df[column],dayfirst=True,errors='coerce').dt.strftime("%Y-%m-%d")
    return df


def apply_karvy_specific_bank_rules(df, map_stage, tenant_id, account_number):
    df['Bank_Name'] = map_stage+" Bank"
    print(f"account number :{account_number}")
    df['Bank Account Number'] = account_number
    tenant_id = 'karvy'
    if map_stage == 'HDFC':
        return hdfc_bank(df,tenant_id,account_number)
    if map_stage == 'YES':
        return yes_bank(df,tenant_id)
    if map_stage == 'CITI':
        return citi_bank(df,tenant_id,account_number)
    if map_stage == 'ICICI':
        return icici_bank(df,tenant_id)
    if map_stage == 'IDBI':
        return idbi_bank(df,tenant_id)
    if map_stage == 'SBI':
        return sbi_bank(df,tenant_id)
    if map_stage == 'SYNDICATE':
        return syndi_bank(df,tenant_id,account_number)
    if map_stage == 'AXIS':
        return axis_bank(df,tenant_id,account_number)
    if map_stage == 'KOTAK':
        return kotak_bank(df,tenant_id)
    
    

# as of now run this...you can combine the run_chained_rules and column_chained rules with small changes
def run_chained_rules_column(file_path, chain_rules, tenant_id, map_stage, look_ups={}, start_rule_id=None):
    """Execute the chained rules column wise"""
    
    
    
    # get the mapping of the rules...basically a rule_id maps to a rule
    rule_id_mapping = {}
    for ind, rule in chain_rules.iterrows():
        rule_id_mapping[rule['rule_id']] = [rule['rule_string'], rule['next_if_sucess'], rule['next_if_failure'], rule['stage'], rule['description'], rule['data_source']]
    logging.info(f"\n rule id mapping is \n{rule_id_mapping}\n")
    
    # evaluate the rules one by one as chained
    # start_rule_id = None
    if start_rule_id is None:
        if rule_id_mapping.keys():
            start_rule_id = list(rule_id_mapping.keys())[0]
    
    BR  = BusinessRules(None, [], {})
    file_name = path_leaf(file_path)[:-4] # stripping the .csv
    file_extension = file_path.split(".")[-1] 
    
    if  file_extension == 'csv':
        BR.data_source['master'] = pd.read_csv(file_path)
    elif file_extension == 'txt':
        BR.data_source['master'] = pd.read_csv(file_path, sep='|')
    elif file_extension == 'xlsx' or file_extension == 'xls' or file_extension == 'xlsm':
        db = DB('business_rules', tenant_id=tenant_id, **db_config)
        sheet_namequery = f"SELECT `sheet_name` FROM `feed_sheet_mapping` WHERE `feed_subfeed` = '{map_stage}'"
        sheet_name_df = db.execute_default_index(sheet_namequery,'karvy_business_rules')
        is_sheet_name = False
        if not sheet_name_df.empty:
            is_sheet_name = True
            sheet_name = sheet_name_df['sheet_name'][0]
            logging.info(f"got the sheet name {sheet_name}")
            
        if is_sheet_name:
            try:
                BR.data_source['master'] = pd.read_excel(file_path, sheet_name)
            except:
                BR.data_source['master'] = pd.read_csv(file_path, sheet_name, sep='\t')
        else:
            try:
                BR.data_source['master'] = pd.read_excel(file_path)
            except:
                BR.data_source['master'] = pd.read_csv(file_path, sep='\t')
        
        for table, holiday_file_path in look_ups.items():
            try:
                BR.data_source[table] = pd.read_excel(holiday_file_path)
            except:
                BR.data_source[table] = pd.read_csv(holiday_file_path, sep='\t')

            #BR.data_source[table] = BR.data_source[table].replace(np.nan, '', regex=True)
            BR.data_source[table] = BR.data_source[table].dropna(axis=0, how='all')

    elif file_extension == 'xlsb':
        df = []

        with open_xlsb(file_path) as wb:
            with wb.get_sheet(1) as sheet:
                for row in sheet.rows():
                    df.append([item.v for item in row])

        df = pd.DataFrame(df[1:], columns=df[0])
        BR.data_source['master'] = df

    


    #BR.data_source['master'] = BR.data_source['master'].replace(np.nan, '', regex=True)
    
    # condition
    bank_stage_query = "SELECT `bank_stages` FROM `bank_stage_details`"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    
    type_ = 'Feed'
    
    if map_stage in json.loads(business_rules_db.execute_default_index(bank_stage_query)['bank_stages'][0]):
        type_ = 'Bank'
        df = get_new_df(BR.data_source['master'], map_stage, tenant_id)
        df = df.dropna(axis=0, how='all')
        account_number = get_account_no(BR.data_source['master'])
        print(f"account_number is {account_number}")
        if account_number == 'column':
            account_query = "SELECT * FROM `Account_number_match`"
            stage_accn_map = json.loads(business_rules_db.execute_default_index(account_query)['banks'][0])
            account_number_column = stage_accn_map[map_stage]
            print(f"account  number {list(df[account_number_column])[0]}")
            account_number = list(df[account_number_column])[0]
        df['Filter'] = 'Y' 
        df['Account Number'] = account_number

        master_df_columns = list(df.columns)
        master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}    
        df =  df.rename(columns=master_df_columns_strip_map) 


        BR.data_source['master'] = generate_feed_sub_feed_bank(df, account_number, map_stage, tenant_id)
        BR.data_source['master'] = apply_karvy_specific_bank_rules(BR.data_source['master'], map_stage, tenant_id, account_number)

    else:

        master_df_columns = list(BR.data_source['master'].columns)
        master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}    
        BR.data_source['master'] =  BR.data_source['master'].rename(columns=master_df_columns_strip_map) 

        # feed wise ....any specific functions ..apply here....
        BR.data_source['master'] = get_new_df(BR.data_source['master'], map_stage, tenant_id)
        BR.data_source['master'] = BR.data_source['master'].dropna(axis=0, how='all')
        BR.data_source['master'] = dateConvertion(BR.data_source['master'],map_stage,tenant_id)
        BR.data_source['master'] = generate_feed_sub_feed(BR.data_source['master'], map_stage, tenant_id)
    

    logging.info(f"\nStart rule id got is {start_rule_id}\n ")
    while start_rule_id != "END" and start_rule_id != None:
        # get the rules, next rule id to be evaluated
        rule_to_evaluate, next_if_sucess, next_if_failure, stage, description, data_source = rule_id_mapping[str(start_rule_id)]  
    
        logging.info(f"\nInside the loop \n rule_to_evaluate  {rule_to_evaluate}\n \
                      \nnext_if_sucess {next_if_sucess}\n \
                      \nnext_if_failure {next_if_failure}\n ")
        
        # evaluate the rule
        BR.rules = [json.loads(rule_to_evaluate)] 
        BR.evaluate_business_rules() # apply the business rules
        start_rule_id = next_if_sucess # no matter what go with next if success
        logging.info(f"\n next rule id to execute is {start_rule_id}\n")
        
    logging.info("\n Applied chained rules successfully")
    # generate the final file name
    file_path_raw_ = file_path[:-4]+"_raw_processed_"+ str(time.mktime(datetime.datetime.today().timetuple()))[:-2]+".csv"
    file_path_standard = file_path[:-4]+"_standard_processed_"+ str(time.mktime(datetime.datetime.today().timetuple()))[:-2]+".csv"
    #updating capture matrix table
    capture_matrix(BR.data_source['master'], file_path_raw_, tenant_id)
    # Getting mapping data
    logging.info("\n Getting Mapping data")
    

    raw_map = None
    # get raw column mapping
    try: 
        db = DB('business_rules', tenant_id=tenant_id, **db_config)
        map_query = f"SELECT `raw_column_mapping` FROM `standard_column_mapping` WHERE `feed_subfeed` = '{map_stage}'"
        raw_map = db.execute_default_index(map_query,'karvy_business_rules')
        raw_map = json.loads(raw_map['raw_column_mapping'][0])
        raw_map = {v:k for k,v in raw_map.items()}
    except Exception as e:
        logging.error("Cannot get mapping data")
        logging.error(e)
    # try: 
    #     db = DB('business_rules', tenant_id=tenant_id, **db_config)
    #     map_query = f"SELECT `raw_column_mapping` FROM `standard_column_mapping` WHERE `feed_subfeed` = '{map_stage}'"
    #     raw_map = db.execute_default_index(map_query,'karvy_business_rules')
    #     raw_map = json.loads(raw_map['mapping'][0])
    # except Exception as e:
    #     logging.error("Cannot get mapping data")
    #     logging.error(e)

    if type_ == 'Feed':
        
        try: 
            db = DB('business_rules', tenant_id=tenant_id, **db_config)
            map_query = f"SELECT `mapping` FROM `standard_column_mapping` WHERE `feed_subfeed` = '{map_stage}'"
            map_ = db.execute_default_index(map_query,'karvy_business_rules')
            map_ = json.loads(map_['mapping'][0])
        except Exception as e:
            logging.error("Cannot get mapping data")
            logging.error(e)
    else:
        feed = list(df['Feed'])[0]
        sub_feed = list(df['Sub_Feed'])[0]
        print (f"banking feed and subfeed are {feed} and {sub_feed}")
        # try: 
        #     db = DB('business_rules', tenant_id=tenant_id, **db_config)
        #     map_query = f"SELECT `map` FROM `bank_column_mapping` WHERE `bank` = '{map_stage}' AND `feed`='{feed}' AND `sub_feed`='{sub_feed}'"
        #     map_ = db.execute_default_index(map_query,'karvy_business_rules')
        #     map_ = json.loads(map_['map'][0])
        # except Exception as e:
        #     logging.error("Cannot get mapping data")
        #     logging.error(e)
        try: 
            db = DB('business_rules', tenant_id=tenant_id, **db_config)
            map_query = f"SELECT `mapping` FROM `standard_column_mapping` WHERE `feed_subfeed` = '{map_stage}'"
            map_ = db.execute_default_index(map_query,'karvy_business_rules')
            map_ = json.loads(map_['mapping'][0])
        except Exception as e:
            logging.error("Cannot get mapping data")
            logging.error(e)

    logging.debug(BR.data_source['master'].columns)
    logging.debug(type_)
    # finally write to the csv
    writeToCsv(BR.data_source['master'], file_path_raw_, file_path_standard, tenant_id, map_stage, raw_map, map_ , type_)
    return BR, file_path_raw_, file_path_standard, type_


def run_chained_rules(case_id, tenant_id, chain_rules, start_rule_id=None, updated_tables=False, trace_exec=None, rule_params=None):
    """Execute the chained rules"""
    
    # get the mapping of the rules...basically a rule_id maps to a rule
    rule_id_mapping = {}
    for ind, rule in chain_rules.iterrows():
        rule_id_mapping[rule['rule_id']] = [rule['rule_string'], rule['next_if_sucess'], rule['next_if_failure'], rule['stage'], rule['description'], rule['data_source']]
    logging.info(f"\n rule id mapping is \n{rule_id_mapping}\n")
    
    # evaluate the rules one by one as chained
    # start_rule_id = None
    if start_rule_id is None:
        if rule_id_mapping.keys():
            start_rule_id = list(rule_id_mapping.keys())[0]
            trace_exec = []
            rule_params = {}
            
    # if start_rule_id then. coming from other service 
    # get the existing trace and rule params data
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)
    rule_data_query = "SELECT * from `rule_data` where `case_id`=%s"
    params = [case_id]
    df = business_rules_db.execute(rule_data_query, params=params)
    try:
        trace_exec = json.loads(list(df['trace_data'])[0])
        logging.info(f"\nexistig trace exec is \n{trace_exec}\n")
    except Exception as e:
        logging.info(f"no existing trace data")
        logging.info(f"{str(e)}")
        trace_exec = []
    
    try:
        rule_params = json.loads(list(df['rule_params'])[0])
        logging.info(f"\nexistig rule_params is \n{rule_params}\n")
    except Exception as e:
        logging.info(f"no existing rule params data")
        logging.info(f"{str(e)}")
        rule_params = {}
       
    logging.info(f"\nStart rule id got is {start_rule_id}\n ")
    while start_rule_id != "END":
        # get the rules, next rule id to be evaluated
        rule_to_evaluate, next_if_sucess, next_if_failure, stage, description, data_source = rule_id_mapping[str(start_rule_id)]  
    
        logging.info(f"\nInside the loop \n rule_to_evaluate  {rule_to_evaluate}\n \
                      \nnext_if_sucess {next_if_sucess}\n \
                      \nnext_if_failure {next_if_failure}\n ")
        
        # update the data_table if there is any change
        case_id_data_tables = get_data_sources(tenant_id, case_id, 'case_id_based')
        master_updated_tables = {} 
        if updated_tables:
            master_updated_tables = get_data_sources(tenant_id, case_id, 'updated_tables')
        # consolidate the data into data_tables
        data_tables = {**case_id_data_tables, **master_data_tables, **master_updated_tables} 
        
        # evaluate the rule
        rules = [json.loads(rule_to_evaluate)] 
        BR  = BusinessRules(case_id, rules, data_tables)
        decision = BR.evaluate_rule(rules[0])
        
        logging.info(f"\n got the decision {decision} for the rule id {start_rule_id}")
        logging.info(f"\n updates got are {BR.changed_fields}")
        
        updates = {}
        # update the updates if any
        if BR.changed_fields:
            updates = BR.changed_fields
            update_tables(case_id, tenant_id, updates)

        
        # update the trace_data
        trace_exec.append(start_rule_id)

        logging.info(f"\n params data used from the rules are \n {BR.params_data}\n")
        # update the rule_params
        trace_dict = {
                        str(start_rule_id):{
                            'description' : description if description else 'No description available in the database',
                            'output' : "",
                            'input' : to_DT_data(BR.params_data['input'])
                            }
                        }
        rule_params.update(trace_dict)
        # update the start_rule_id based on the decision
        if decision:
            start_rule_id = next_if_sucess
        else:
            start_rule_id = next_if_failure
        logging.info(f"\n next rule id to execute is {start_rule_id}\n")
        
    
    # off by one updates...
    trace_exec.append(start_rule_id)
    
    # store the trace_exec and rule_params in the database
    update_rule_params_query = f"INSERT INTO `rule_data`(`id`, `case_id`, `rule_params`) VALUES ('NULL',%s,%s) ON DUPLICATE KEY UPDATE `rule_params`=%s"
    params = [case_id, json.dumps(rule_params), json.dumps(rule_params)]
    business_rules_db.execute(update_rule_params_query, params=params)
    
    update_trace_exec_query = f"INSERT INTO `rule_data` (`id`, `case_id`, `trace_data`) VALUES ('NULL',%s,%s) ON DUPLICATE KEY UPDATE `trace_data`=%s"
    params = [case_id, json.dumps(trace_exec), json.dumps(trace_exec)]
    business_rules_db.execute(update_trace_exec_query, params=params)
    
    logging.info("\n Applied chained rules successfully")
    return 'Applied chained rules successfully'

def run_group_rules(case_id, rules, data):
    """Run the rules"""
    rules = [json.loads(rule) for rule in rules] 
    BR  = BusinessRules(case_id, rules, data)
    updates = BR.evaluate_business_rules()
    logging.info(f"\n updates from the group rules are \n{updates}\n")
    return updates

def apply_business_rule(case_id, function_params, tenant_id, file_path, stage=None, look_ups={}):
    """Run the business rules based on the stage in function params and tenant_id
    Args:
        case_id: Unique id that we pass
        function_params: Parameters that we get from the configurations
        tenant_id: Tenant on which we have to apply the rules
    Returns:
    """
    updates = {} # keep a track of updates that are being made by business rules
    try:
        # get the stage from the function_parameters...As of now its first ele..
        # need to make generic or key-value pairs
        logging.info(f"\n case_id {case_id} \nfunction_params {function_params} \ntenant_id {tenant_id}\n")
        if not stage:
            try:
                stage = function_params['stage'][0]
            except Exception as e:
                logging.error(f"\n error in getting the stage \n")
                
                stage = 'cms'
        logging.info(f"\n got the stage {stage} \n")

        
        # no case id passed meaning the operations we are doing on the column wise not case_id wise .
        # feature developed for karvy
        column = False
        if not case_id:
            column = True
        
        logging.info(f"\n Had to apply the column rules because colum bool is {stage} \n")
        # get the rules
        rules = get_rules(tenant_id, stage)
        

        # get the mapping of the rules...basically a rule_id maps to a rule.
        # useful for the chain rule evaluations
        rule_id_mapping = {}
        for ind, rule in rules.iterrows():
            rule_id_mapping[rule['rule_id']] = [rule['rule_string'], rule['next_if_sucess'], rule['next_if_failure'], rule['stage'], rule['description'], rule['data_source']]

        # if columwise processing then run those
        if column:
            output, file_name_raw,file_name_standard, type_  = run_chained_rules_column(file_path, rules, tenant_id, stage, look_ups=look_ups)
            kafka_data = {'standard_processed_file_path':file_name_standard, 'raw_processed_file_path':file_name_raw, 'stage':stage, 'type':type_}
            return {'flag': True, 'message': 'Applied business rules columnwise successfully.', 'produce_data':kafka_data, 'output':output}

            
        # making it generic takes to take a type parameter from the database..
        # As of now make it (all others  or chained) only
        is_chain_rule = '' not in rule_id_mapping
        
        # get the required table data on which we will be applying business_rules  
        case_id_data_tables = get_data_sources(tenant_id, case_id, 'case_id_based') 
        master_data_tables = get_data_sources(tenant_id, case_id, 'master', master=True)
        
        # consolidate the data into data_tables
        data_tables = {**case_id_data_tables, **master_data_tables} 
        
        logging.info(f"\ndata got from the tables is\n")
        logging.info(data_tables)
        
        updates = {}
        # apply business rules
        if is_chain_rule:
            run_chained_rules(case_id, tenant_id, rules)
        else:
            updates = run_group_rules(case_id, list(rules['rule_string']), data_tables)
            
        # update in the database, the changed fields eventually when all the stage rules were got
        update_tables(case_id, tenant_id, updates)
        
        #  return the updates for viewing
        return {'flag': True, 'message': 'Applied business rules successfully.', 'updates':updates}
    except Exception as e:
        logging.exception('Something went wrong while applying business rules. Check trace.')
        return {'flag': False, 'message': 'Something went wrong while applying business rules. Check logs.', 'error':str(e)}

In [77]:
case_id = None
function_params = {'stage':['CPVIRTUAL_SA99']}
tenant_id = 'karvy'
file_path = '/home/ubuntu/Downloads/ak991.xlsx'
kotak = "/home/ubuntu/Downloads/banks/kotak.xls"
wi99 = "/home/ubuntu/Downloads/wi99.xls"
invezta = "/home/ubuntu/Downloads/invezta.xls"
cg99 = "/home/ubuntu/Downloads/cg99.xlsx"
sa99 = "/home/ubuntu/Downloads/sa99.xlsx"
look_ups = {'holiday1':"C:\\Users\\Algonox\\Desktop\\AlgonoxWork\\TestBusinessRulesModule\\holiday1.xlsx",
           'holiday2':"C:\\Users\\Algonox\\Desktop\\AlgonoxWork\\TestBusinessRulesModule\\holiday2.xlsx"}

r = apply_business_rule(case_id, function_params, tenant_id, sa99, look_ups={})

INFO:root:
 case_id None 
function_params {'stage': ['CPVIRTUAL_SA99']} 
tenant_id karvy

INFO:root:
 got the stage CPVIRTUAL_SA99 

INFO:root:
 Had to apply the column rules because colum bool is CPVIRTUAL_SA99 

INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (4.74 secs to connect)
DEBUG:root:Query: SELECT * from `sequence_rule_data` where `group` = %s
INFO:root:
 rule id mapping is 
{'76': ['{"rule_type": "static", "function": "Assign", "parameters": {"assign_table": {"table": "master", "column": "Scheme Code"}, "assign_value": {"source": "rule", "value": {"rule_type": "static", "function": "GetRange", "parameters": {"value": {"source": "input_config", "table": "master", "column": "Scheme Code"}, "range": {"st

INFO:root:
Evaluating the rule 
{'rule_type': 'static', 'function': 'Assign', 'parameters': {'assign_table': {'table': 'master', 'column': 'Filter'}, 'assign_value': {'source': 'rule', 'value': {'rule_type': 'static', 'function': 'WhereClause', 'parameters': {'data_frame1': {'source': 'input_config', 'table': 'master', 'column': 'Filter'}, 'data_frame2': {'source': 'rule', 'value': {'rule_type': 'static', 'function': 'TransformDF', 'parameters': {'table': 'master', 'value1_column': {'source': 'input', 'value': 'UTR NO'}, 'operator': 'broadcast', 'value2': {'source': 'input', 'value': 'N'}}}}, 't_value': {'source': 'rule', 'value': {'rule_type': 'static', 'function': 'IsAlnum', 'parameters': {'from_table': 'master', 'column_name': 'UTR NO'}}}}}}}}

DEBUG:root:parameters got are {'assign_table': {'table': 'master', 'column': 'Filter'}, 'assign_value': {'source': 'rule', 'value': {'rule_type': 'static', 'function': 'WhereClause', 'parameters': {'data_frame1': {'source': 'input_config', 't

DEBUG:root:Feed
INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`


required standard mapping got is
{'Feed': 'Feed', 'Sub_Feed': 'Sub_Feed', 'Credit Date': 'Date', 'UTR NO': 'Code', 'Filter': 'Filter', 'Amount': 'Amount', 'Matched': 'Matched'}


INFO:root:Connection established succesfully to `karvy_business_rules`! (4.69 secs to connect)
DEBUG:root:Index(['Channel Partner', 'Channel Partner name', 'AMC CODE', 'Scheme Code', 'TXN ID', 'Investor Name', 'Count', 'Account No', 'Amount', 'Pmt Mode', 'Ecs sataus', 'Trxn Date', 'Credit Date', 'UTR NO', 'Filter', 'Matched', 'ID', 'Sub_Feed', 'Feed', 'Feed_ID'], dtype='object')
DEBUG:root:Feed
INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`


Index(['Channel Partner', 'Channel Partner name', 'AMC CODE', 'Scheme Code', 'TXN ID', 'Investor Name', 'Count', 'Account No', 'Amount', 'Pmt Mode', 'Ecs sataus', 'Trxn Date', 'Credit Date', 'UTR NO', 'Filter', 'Matched', 'ID', 'Sub_Feed', 'Feed', 'Feed_ID'], dtype='object')
Index(['Channel Partner', 'Channel Partner name', 'AMC CODE', 'Scheme Code', 'TXN ID', 'Investor Name', 'Count', 'Account No', 'Amount', 'Pmt Mode', 'Ecs sataus', 'Trxn Date', 'Credit Date', 'UTR NO', 'Filter', 'Matched', 'ID', 'Sub_Feed', 'Feed', 'Feed_ID'], dtype='object')
['Feed_ID', 'Raw_Id', 'case_id', 'Channel Partner', 'Channel Partner name', 'AMC CODE', 'Scheme Code', 'TXN ID', 'Investor Name', 'Count', 'Account No', 'Amount', 'Pmt Mode', 'Ecs sataus', 'Trxn Date', 'Credit Date', 'UTR NO', 'Filter', 'Matched', 'queue']


INFO:root:Connection established succesfully to `karvy_business_rules`! (4.81 secs to connect)


In [78]:
r['output'].data_source['master']

Channel Partner                   Channel Partner name AMC CODE Scheme Code      TXN ID    Investor Name  Count    Account No   Amount Pmt Mode Ecs sataus   Trxn Date Credit Date            UTR NO Filter  Matched  ID        Sub_Feed       Feed                       Feed_ID                        Raw_Id                       case_id
0            1128.0  Sarsa Financial Advisory Services Ltd      MAF          IO    528252.0    Lbqjm Svtubhj    1.0  6.003501e+11   2000.0      SIP        ECS  2019-06-15  2019-06-17  ICIB191680006671      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_142  CPVIRTUAL_CPVIRTUAL_SA99_142  CPVIRTUAL_CPVIRTUAL_SA99_142
2            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10062461.0  Sjuv Nbiftixbsj    1.0  6.003501e+11   1000.0      SIP        ECS  2019-06-15  2019-06-17  AXISP00057084526      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_144  CPVIRTUAL_CPVIRTUAL_SA99_144  CPVIRTUAL_CPVIRTUAL_SA99_144
4            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10022888.0   Lpvtijl Tbslbs    1.0  6.003501e+11   2000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_146  CPVIRTUAL_CPVIRTUAL_SA99_146  CPVIRTUAL_CPVIRTUAL_SA99_146
5            1128.0  Sarsa Financial Advisory Services Ltd      MAF          IO  10048644.0    Qsjzbol Tjoib    1.0  6.003501e+11   1500.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_147  CPVIRTUAL_CPVIRTUAL_SA99_147  CPVIRTUAL_CPVIRTUAL_SA99_147
6            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10059379.0     Svdij Lboxbs    1.0  6.003501e+11   3000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_148  CPVIRTUAL_CPVIRTUAL_SA99_148  CPVIRTUAL_CPVIRTUAL_SA99_148
7            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10088612.0   Tiflibs Tibsnb    1.0  6.003501e+11   1500.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_149  CPVIRTUAL_CPVIRTUAL_SA99_149  CPVIRTUAL_CPVIRTUAL_SA99_149
8            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10091552.0    Joesb Dibvibo    1.0  6.003501e+11   3000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_150  CPVIRTUAL_CPVIRTUAL_SA99_150  CPVIRTUAL_CPVIRTUAL_SA99_150
9            1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10094048.0    Tbokbz Uibmps    1.0  6.003501e+11   2000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_151  CPVIRTUAL_CPVIRTUAL_SA99_151  CPVIRTUAL_CPVIRTUAL_SA99_151
10           1128.0  Sarsa Financial Advisory Services Ltd      MAF          EB  10130875.0      Mbmju Lvnbs    1.0  6.003501e+11   1000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_152  CPVIRTUAL_CPVIRTUAL_SA99_152  CPVIRTUAL_CPVIRTUAL_SA99_152
11           1128.0  Sarsa Financial Advisory Services Ltd      MAF          IO  10158851.0   Tboeffq Nbibmb    1.0  6.003501e+11   5000.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_153  CPVIRTUAL_CPVIRTUAL_SA99_153  CPVIRTUAL_CPVIRTUAL_SA99_153
12           1128.0  Sarsa Financial Advisory Services Ltd      MAF          IO  10169739.0   Effqjlb Libusj    1.0  6.003501e+11   1500.0      SIP        ACH  2019-06-15  2019-06-17  ICIB191680022467      Y        0   0  CPVIRTUAL_SA99  CPVIRTUAL  CPVIRTUAL_CPVIRTUAL_SA99_154  CPVIRTU

In [7]:
def kotak_code_apply(row):
    if row['Filter'] == 'N':
        return row
    try:
        
        if str(row['Account No']) == '09582540006664':
            row['Code'] = row['Chq / Ref number'].str.split("-").index[1]
            return row
        if str(row['Account No']) == '9312739875':
            row['Code'] = row['Description']
            return row
    except:
        return row
    
    return row

In [9]:
def kotak_bank(kotak_df,tenant_id):
    kotak_df = dateConvertion(df, map_stage, tenant_id)
    kotak_df['Code'] = ''
    
    kotak_df['Account No'] = account_number
    kotak_df['Filter'] = kotak_df['Filter'].where(~kotak_df['Deposit'].isnull(), 'N')
    kotak_df['Value Date'] = pd.to_datetime(kotak_df[column],  errors='coerce')
    kotak_df['Time'] = kotak_df['Value Date'].dt.time
    kotak_df['Value Date'] = pd.to_datetime(kotak_df['Value Date'].dt.strftime('%Y-%m-%d'))
    
    
    return kotak_df

In [10]:
# df['Account No'] = account_number
df['Account No'] = '09582540006664'
df['Code'] = ''
df.apply(kotak_code_apply, axis=1)
# df['Chq / Ref number'].str.split('-')
np.where(df['Value Date'] == '2019-06-03', '','d')



NameError: name 'df' is not defined

In [77]:
df

'ASDFDSAFDFDASFDAFASDFSFDA'

In [28]:
df  =dateConvertion(df, map_stage, tenant_id)


INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (19.76 secs to connect)


In [11]:
def code_apply(row):
    
    if row['Feed'].lower() == 'CPVIRTUAL'.lower():
        if str(row['Sub_Feed']) in ['CPVIRTUAL_LI99', 'CPVIRTUAL_IO99', 'CPVIRTUAL_AK99']:
            row['Code'] = row['Reference No.']
            return row
    return row

In [12]:
kotak = "/home/ubuntu/Downloads/banks/kotak.xls"
map_stage = 'KOTAK'
df = pd.read_excel(kotak)

master_df_columns = list(df.columns)
master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}    
df =  df.rename(columns=master_df_columns_strip_map) 


account_number = get_account_no(df)
print(f"account_number is {account_number}")

df = get_new_df(df, map_stage, tenant_id)

INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`


account_number is 09582540007788


INFO:root:Connection established succesfully to `karvy_business_rules`! (4.57 secs to connect)


['Sl. No.', 'Date', 'Description', 'Chq / Ref number', 'Value Date', 'Withdrawal', 'Deposit', 'Balance', 'CR/DR']


In [13]:
df['Value Date']

11     2019-06-03 00:00:00
12     2019-06-03 00:00:00
13     2019-06-03 00:00:00
14                     NaN
15     2019-06-04 00:00:00
              ...         
132    2019-06-28 00:00:00
133    2019-06-28 00:00:00
134    2019-06-28 00:00:00
135                    NaN
136    2019-06-29 00:00:00
Name: Value Date, Length: 126, dtype: object

In [14]:
df['Filter'].iloc[0] = 'N'
# df[df['Filter'] == 'Y']['Description']
df['Code']  = 

SyntaxError: invalid syntax (<ipython-input-14-79a1d4a69a12>, line 3)

In [ ]:
kotak = "/home/ubuntu/Downloads/banks/syndicate.xls"
map_stage = 'KOTAK'
df = pd.read_excel(kotak)

# master_df_columns = list(df.columns)
# master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}    
# df =  df.rename(columns=master_df_columns_strip_map) 


account_number = get_account_no(df)
print(f"account_number is {account_number}")

df = get_new_df(df, map_stage, tenant_id)
master_df_columns = list(df.columns)
master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}    
df =  df.rename(columns=master_df_columns_strip_map) 
df = df.dropna(axis=0, how='all')


if account_number == 'column':
    account_query = "SELECT * FROM `Account_number_match`"
    stage_accn_map = json.loads(business_rules_db.execute_default_index(account_query)['banks'][0])
    account_number_column = stage_accn_map[map_stage]
    print(f"account  number {list(df[account_number_column])[0]}")
    account_number = list(df[account_number_column])[0]

print ("FINAL ACCOUNT NUMBER", account_number)
df['Filter'] = 'Y' 
df = generate_feed_sub_feed_bank(df, account_number, map_stage, tenant_id)
# df = apply_karvy_specific_bank_rules(df, map_stage, tenant_id, account_number)









In [1]:
master_df_columns = (r['output'].data_source['master'].columns)

# master_df_columns_strip_map = {ele:ele.strip() for ele in master_df_columns}

# print (master_df_columns_strip_map)

d = r['output'].data_source['master']
# r['output'].data_source['master']
# r
d['Credit TS']

NameError: name 'r' is not defined

In [ ]:
[ele.strip() for ele in list(r['output'].data_source['master'].columns)]

In [ ]:


wi99 = "/home/ubuntu/Downloads/wi99.xls"
wi99_df = pd.read_excel(wi99, sheet_name='Details')

wi99_df = get_new_df(wi99_df, 'Direct Credits - WI99', tenant_id)
wi99_df.dropna(axis=0, how='all')

In [17]:
name = "/home/ubuntu/Downloads/junk_test.xlsx"
s = pd.read_excel(name)
s = 
get_new_df(s, 'CPVIRTUAL_MB99', tenant_id)


SyntaxError: invalid syntax (<ipython-input-17-99a52b61c0b7>, line 3)

In [18]:
ak99 = "/home/ubuntu/Downloads/test_date.xlsx"
df = pd.read_excel(ak99, parse_dates=False)

# df['Credit Date'] = pd.to_datetime(df['Credit Date'])
# # df.replace(np.nan, '0000-00-00', regex=True)
# # df['Credit Date'].replace(np.nan, '')
# df['Credit Date'].astype(str).str.split().str[0]
df

RIA_code    AMC scheme_code pm_payment_method  folio_number  \
0     INA100009859  MIRAS        TSD1               UPI  7.991896e+10   
1     INA100009859  MIRAS        TSD1        NETBANKING  7.991863e+10   
2     INA100009859  MIRAS        TSD1               UPI  7.991689e+10   
3     INA100009859  MIRAS        IOD1        NETBANKING  7.991918e+10   
4     INA100009859  MIRAS        TSD1               UPI  7.991853e+10   
...            ...    ...         ...               ...           ...   
2016  INA100009859  MIRAS        TSD1               UPI  7.991680e+10   
2017  INA100009859  MIRAS        EBD1        NETBANKING           NaN   
2018  INA100009859  MIRAS        EBD1        NETBANKING  7.991779e+10   
2019  INA100009859  MIRAS        IOD1        NETBANKING  7.991676e+10   
2020  INA100009859  MIRAS        TSD1        NETBANKING  7.991464e+10   

               pm_transaction_id user_code           Investor_Name  \
0     P-MF-MIRAS-K-120619-257204   PAYTMMU          TBJLBU  TBSLBS   
1     P-MF-MIRAS-K-120619-259882   PAYTMMU  SBWJOEFS LVNBS  KVOFKB   
2     P-MF-MIRAS-K-120619-258209   PAYTMMU           Blbotib  Sboj   
3     P-MF-MIRAS-K-120619-259662   PAYTMMU            BCIJKJU  SPZ   
4     P-MF-MIRAS-K-120619-260948   PAYTMMU          Bovsbh  Lvnbs    
...                          ...       ...                     ...   
2016  P-MF-MIRAS-K-150619-249305   PAYTMMU  Ubqbti Sbnblbou  Qboeb   
2017  P-MF-MIRAS-K-150619-252094   PAYTMMU       C CBSBUI  QBOEJBO   
2018  P-MF-MIRAS-K-150619-261026   PAYTMMU         TIVCISBOJM  EBT   
2019  P-MF-MIRAS-K-150619-265771   PAYTMMU          TISFZFT  WFSNB   
2020  P-MF-MIRAS-K-150619-256133   PAYTMMU      WFE QSBLBTI  TJOHI   

         transaction_date transaction_time   rta_ref_no  amount  user_trxn_no  \
0     2019-12-06 00:00:00         11:07:36  106406670.0    1000        257204   
1     2019-12-06 00:00:00         11:59:11  106411328.0   25000        259882   
2     2019-12-06 00:00:00         11:45:17  106409611.0    1000        258209   
3     2019-12-06 00:00:00         09:48:09  106403798.0    5000        259662   
4     2019-12-06 00:00:00         10:14:20  106403973.0    2500        260948   
...                   ...              ...          ...     ...           ...   
2016           14/06/2019         11:45:29  106487625.0    1000        249305   
2017           14/06/2019         11:43:33  106487650.0    1000        252094   
2018           14/06/2019         07:17:57  106487847.0    1000        261026   
2019           14/06/2019         07:27:59  106487217.0    5000        265771   
2020           14/06/2019         08:50:38  106487626.0    2000        256133   

            utr_Number  
0     CITIN19986613340  
1     CITIN19986613340  
2     CITIN19986613340  
3     CITIN19986613340  
4     CITIN19986613340  
...                ...  
2016  CITIN19987693206  
2017  CITIN19987693206  
2018  CITIN19987693206  
2019  CITIN19987693206  
2020  CITIN19987693206  

[2021 rows x 14 columns]

In [19]:
pd.to_datetime(df['transaction_date'])

0      2019-12-06
1      2019-12-06
2      2019-12-06
3      2019-12-06
4      2019-12-06
          ...    
2016   2019-06-14
2017   2019-06-14
2018   2019-06-14
2019   2019-06-14
2020   2019-06-14
Name: transaction_date, Length: 2021, dtype: datetime64[ns]

In [41]:
import pandas as pd

def get_new_df(df,stage, tenant_id, threshold=0.6):
    df = df.dropna(axis=1, how='all')
    header_map_query = "SELECT `headers` FROM `bank_headers_mapping` where BANK=%s"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)

    headers_df = business_rules_db.execute_default_index(header_map_query, params=[stage])
    
    if not headers_df.empty:
        headers = json.loads(headers_df['headers'][0])
        print (headers)
        for index, row in df.iterrows():
            key = stage
            values = headers
            strips_rows = [str(ele).strip() for ele in list(row)]
            strip_values = [str(ele).strip() for ele in values]
            strip_rows_string = ' '.join([str(ele).strip() for ele in list(row)])
            strip_values_string = ' '.join(values)
            print (difflib.SequenceMatcher(None, strip_rows_string, strip_values_string))

            if (strips_rows[0] == strip_values[0] and strips_rows[1] == strip_values[1]):

                new_header = df.iloc[index] #grab the first row for the header
                df = df[index+1:] #take the data less the header row
                df.columns = new_header #set the header row as the df header
                return df
    df = df.dropna(axis=0, how='all')
    return df



In [21]:
text = "/home/ubuntu/Downloads/mfu.xls"
text_df = pd.read_excel(text)

In [22]:
text_df

BTRN          FTRN AMC Code                 AMC Name  \
0    201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
1    201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
2    201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
3    201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
4    201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
..            ...           ...      ...                      ...   
140  201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
141  201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
142  201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
143  201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   
144  201906010210  190601MAF001      MAF  MIRAE ASSET MUTUAL FUND   

    RTA Scheme Code                                   Scheme Plan Name  \
0             CFD1G  Mirae Asset Cash Management Fund - Direct Plan...   
1             IOD1G      Mirae Asset Large Cap Fund Direct Plan Growth   
2             ICRGG   Mirae Asset Great Consumer Fund - Regular Growth   
3             TSD1G         Mirae Asset Tax Saver Fund - Direct Growth   
4             IOD1G      Mirae Asset Large Cap Fund Direct Plan Growth   
..              ...                                                ...   
140           TSD1G         Mirae Asset Tax Saver Fund - Direct Growth   
141           IOD1G      Mirae Asset Large Cap Fund Direct Plan Growth   
142           LPIGG  Mirae Asset Savings Fund - Regular Savings Gro...   
143           FFRGG     Mirae Asset Focused Fund - Regular Plan Growth   
144           LPIGG  Mirae Asset Savings Fund - Regular Savings Gro...   

       CAN No\t          Folio No\t  \
0    15037QZA24  79911002304          
1    15055RAA37  79914691644          
2    15161RAA15                       
3    15211RAA09  7922477363           
4    15335JCA01  79911156824          
..          ...                 ...   
140  19146QZ01X                       
141  19147QZ01Y  79918605863          
142  19150RB02B                       
143  19151QZ01Q                       
144  19151QZ01Q                       

                                           Holder Name             GORN   ...  \
0    LBOOBO TVCCJBI                                ...  15037QZA24000358  ...   
1    HBKFOESB LVNBS NBMBW                          ...  15055RAA37000242  ...   
2    TSJOJWBT BMVSJ                                ...  15161RAA15000025  ...   
3    TBDIJO DIPQSB                                 ...  15211RAA09000035  ...   
4    TIFFNB CIBUJB                                 ...  15335JCA01000061  ...   
..                                                 ...               ...  ...   
140  L WJKBZBSBHIBWBO                              ...  19146QZ01X000002  ...   
141  BZVTI LVNBS TFO                               ...  19147QZ01Y000002  ...   
142  TXBQOBHBVSJ QBUXBSEIBO                        ...  19150RB02B000001  ...   
143  QSJZBOLB TVSZBLBOU  LBMCIPS                   ...  19151QZ01Q000001  ...   
144  QSJZBOLB TVSZBLBOU  LBMCIPS                   ...  19151QZ01Q000002  ...   

    Source Bank Code  Source Bank MICR             Source Bank Name  \
0                485         400485002  KOTAK MAHINDRA BANK LIMITED   
1                485         400485002  KOTAK MAHINDRA BANK LIMITED   
2                485         400485002  KOTAK MAHINDRA BANK LIMITED   
3                485         400485002  KOTAK MAHINDRA BANK LIMITED   
4                485         400485002  KOTAK MAHINDRA BANK LIMITED   
..               ...               ...                          ...   
140              485         400485002  KOTAK MAHINDRA BANK LIMITED   
141              485         400485002  KOTAK MAHINDRA BANK LIMITED   
142              485         400485002  KOTAK MAHINDRA BANK LIMITED   
143              485         400485002  KOTAK MAHINDRA BANK LIMITED   
144              485         400485002  KOTAK MAHINDRA BANK LIMITED   



In [14]:
import pandas as pd

file_path = "/home/ubuntu/Downloads/hdfc.xlsm"
hdfc_df = pd.read_excel(file_path)
print (len(hdfc_df))
hdfc_df = get_new_df(hdfc_df, 'HDFC', 'karvy')
hdfc_df['Code'] = hdfc_df['Transaction Description']
hdfc_df['Filter'] = 'Y'

account_no_filter_map = {
            "600350117285":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "57500000197162":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "57500000207581":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "600350087152":["MAMFIO","MAMFCM","MAMFEB","MAMFPF","MAMFFS","MAMFTF","MAMFSB","MAMFGF","MAMFUS","MIRAEFNX","MAMFHC","MAMFEQSA","MAMFDB","MAMFMC"],
            "990620012131":["PAY-OUT","00990640000982"],
            "600350051109":["50200009635552"],
            "990610016361":["MFSS Normal Pay-out S"],
            "602090003198":["KARVY DATA MAN"],
            "57500000090687":["Mirae Asset ISIP Collection"],
            "57500000090303":["MIRAE ASSET SIP COLLECTION"]

        }
    
#     hdfc_df = generate_feed_id(hdfc_df, 'HDFC', tenant_id, type_='Bank')
hdfc_df = filter_rows(hdfc_df, '600350117285', account_no_filter_map, 'Transaction Description')


INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`


1834


INFO:root:Connection established succesfully to `karvy_business_rules`! (4.58 secs to connect)


['Transaction Date', 'Value Date', 'Transaction Amount', 'Debit / Credit', 'Transaction Description', 'Reference No.', 'Transaction Branch', 'Running Balance']
HEREEEEEE
MAMFIO
9       False
10       True
11      False
12      False
13      False
        ...  
1829    False
1830    False
1831     True
1832    False
1833    False
Name: Transaction Description, Length: 1825, dtype: bool
HEREEEEEE
MAMFCM
9       False
10      False
11      False
12      False
13      False
        ...  
1829    False
1830     True
1831    False
1832    False
1833    False
Name: Transaction Description, Length: 1825, dtype: bool
HEREEEEEE
MAMFEB
9        True
10      False
11      False
12       True
13      False
        ...  
1829    False
1830    False
1831    False
1832     True
1833    False
Name: Transaction Description, Length: 1825, dtype: bool
HEREEEEEE
MAMFPF
9       False
10      False
11      False
12      False
13       True
        ...  
1829    False
1830    False
1831    False
1832    False

In [16]:
hdfc_df

8        Transaction Date           Value Date Transaction Amount  \
9     2019-06-01 12:03:09  2019-06-01 00:00:00               3000   
10    2019-06-01 16:35:55  2019-06-01 00:00:00               1000   
11                    NaN                  NaN                NaN   
12    2019-06-01 16:35:55  2019-06-01 00:00:00               2000   
13    2019-06-01 16:35:55  2019-06-01 00:00:00              10000   
...                   ...                  ...                ...   
1829  2019-06-29 20:18:11  2019-06-29 00:00:00            7097000   
1830  2019-06-29 20:18:11  2019-06-29 00:00:00           10535000   
1831  2019-06-29 20:18:11  2019-06-29 00:00:00           12190100   
1832  2019-06-29 20:41:02  2019-06-29 00:00:00               5000   
1833  2019-06-29 20:41:02  2019-06-29 00:00:00               5000   

8    Debit / Credit            Transaction Description Reference No.  \
9                 C  CMS-MAMFEB-190601000005/MOD/HBTRF  190601000005   
10                C    CMS-MAMFIO-190601000012/MOD/LCT  190601000012   
11              NaN                                NaN           NaN   
12                C    CMS-MAMFEB-190601000012/MOD/LCT  190601000012   
13                C    CMS-MAMFPF-190601000012/MOD/LCT  190601000012   
...             ...                                ...           ...   
1829              C       CMS-MAMFFS-190629000017/MOD/  190629000017   
1830              C       CMS-MAMFCM-190629000017/MOD/  190629000017   
1831              C       CMS-MAMFIO-190629000017/MOD/  190629000017   
1832              C    CMS-MAMFEB-190629000018/MOD/LCT  190629000018   
1833              C    CMS-MAMFTF-190629000018/MOD/LCT  190629000018   

8    Transaction Branch Running Balance                               Code  \
9           KANJUR MARG        80228850  CMS-MAMFEB-190601000005/MOD/HBTRF   
10          KANJUR MARG        80229850    CMS-MAMFIO-190601000012/MOD/LCT   
11                  NaN             NaN                                NaN   
12          KANJUR MARG        80231850    CMS-MAMFEB-190601000012/MOD/LCT   
13          KANJUR MARG        80241850    CMS-MAMFPF-190601000012/MOD/LCT   
...                 ...             ...                                ...   
1829        KANJUR MARG       134499335       CMS-MAMFFS-190629000017/MOD/   
1830        KANJUR MARG       145034335       CMS-MAMFCM-190629000017/MOD/   
1831        KANJUR MARG       157224435       CMS-MAMFIO-190629000017/MOD/   
1832        KANJUR MARG       157229435    CMS-MAMFEB-190629000018/MOD/LCT   
1833        KANJUR MARG       157234435    CMS-MAMFTF-190629000018/MOD/LCT   

8    Filter  
9         Y  
10        Y  
11        Y  
12        Y  
13        Y  
...     ...  
1829      Y  
1830      Y  
1831      N  
1832      Y  
1833      Y  

[1825 rows x 10 columns]

In [38]:
file_path = "/home/ubuntu/Downloads/format_test.xlsb"
df = []
with open_xlsb(file_path) as wb:
            with wb.get_sheet(1) as sheet:
                for row in sheet.rows():
                    df.append([item.v for item in row])

df = pd.DataFrame(df[1:], columns=df[0])


TypeError: get_new_df() missing 2 required positional arguments: 'stage' and 'tenant_id'

In [15]:
# hdfc_df
def filter_rows(df, account_no, account_no_filter_map, filter_field):
    filter_values = []
    if account_no in account_no_filter_map:
        filter_values = account_no_filter_map[account_no]
    t_value = pd.Series([True]*len(df))
    for val in filter_values:
        print ("HEREEEEEE")
        print (val)
        print (df[filter_field].astype(str).str.contains(val))
        t_value = t_value | df[filter_field].astype(str).str.contains(val)
    df['Filter'] = df['Filter'].where(t_value, 'N')

    return df

In [24]:
hdfc_df = hdfc_df.dropna(axis=0, how='all')
# (pd.to_datetime(hdfc_df['Transaction Date']).dt.strftime('%d-%m-%Y'))

# list(pd.to_datetime(hdfc_df['Value Date']).dt.strftime('%d-%m-%Y'))
pd.to_datetime(hdfc_df['Value Date'], dayfirst=True)

9      2019-06-01
10     2019-06-01
12     2019-06-01
13     2019-06-01
14     2019-06-01
          ...    
1829   2019-06-29
1830   2019-06-29
1831   2019-06-29
1832   2019-06-29
1833   2019-06-29
Name: Value Date, Length: 1807, dtype: datetime64[ns]

In [58]:
file_path = "/home/ubuntu/Downloads/format_test.xlsb"
df = []
with open_xlsb(file_path) as wb:
            with wb.get_sheet(1) as sheet:
                for row in sheet.rows():
                    df.append([item.v for item in row])

df = pd.DataFrame(df[1:], columns=df[0])
df
get_new_df(df)

TypeError: get_new_df() missing 2 required positional arguments: 'stage' and 'tenant_id'

In [50]:
import pandas as pd

def get_new_df(df,stage, tenant_id, threshold=0.6):
    df = df.dropna(axis=1, how='all')
    header_map_query = "SELECT `headers` FROM `bank_headers_mapping` where BANK=%s"
    business_rules_db = DB('business_rules', tenant_id=tenant_id, **db_config)

    headers_df = business_rules_db.execute_default_index(header_map_query, params=[stage])
    
    if not headers_df.empty:
        headers = json.loads(headers_df['headers'][0])
        print (headers)
        for index, row in df.iterrows():
            key = stage
            values = headers
            strips_rows = [str(ele).strip() for ele in list(row)]
            strip_values = [str(ele).strip() for ele in values]
            strip_rows_string = ' '.join([str(ele).strip() for ele in list(row)])
            strip_values_string = ' '.join(values)
            print (strip_rows_string)
            print (strip_values_string)
            print (difflib.SequenceMatcher(None, strip_rows_string, strip_values_string).ratio())

            if (strips_rows[0] == strip_values[0] and strips_rows[1] == strip_values[1]):

                new_header = df.iloc[index] #grab the first row for the header
                df = df[index+1:] #take the data less the header row
                df.columns = new_header #set the header row as the df header
                return df
    df = df.dropna(axis=0, how='all')
    return df



In [51]:
import pandas as pd
pd.set_option('display.max_rows', 50000000)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [54]:
axis = "/home/ubuntu/Downloads/June download statements/Axis/axis.xls"

In [55]:
import difflib
axis_df = pd.read_excel(axis)
get_new_df(axis_df, 'AXIS', 'karvy')
# axis_df

INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (6.31 secs to connect)


['Tran Date', 'Value Date', 'CHQNO', 'Transaction Particulars', ' Amount(INR)', 'DR|CR', 'Balance(INR)', 'Branch Name']
Joint Holder :-- nan nan nan nan nan nan nan nan
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.2112676056338028
MIRAESSET GLOBAL INVESTMENT,MAG INDIS P LTD, nan nan nan nan nan nan nan nan
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.17647058823529413
UNIT-606,6TH FLR,WINDSOR OFFCST RD,KALINA nan nan nan nan nan nan nan nan
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.17964071856287425
MUMBAI nan nan nan nan nan nan nan nan
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.21212121212121213
MAHARASHTRA nan nan nan nan nan nan nan nan
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.21897810218978103
400078 nan nan nan nan 

0.13559322033898305
377 20-09-2019 20-09-2019 14:44:09 nan ICONN/691696114/913010004211574/200919/1100000000 nan 10000.00 6326302.11 224
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10476190476190476
378 20-09-2019 20-09-2019 14:47:29 nan TRF/PARAG MAHESHWARI/ nan 1200000.00 7526302.11 361
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.09782608695652174
379 20-09-2019 20-09-2019 14:49:19 nan ICONN/691697455/910010035657959/200919/1100000000 nan 700000.00 8226302.11 1161
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10377358490566038
380 20-09-2019 20-09-2019 15:44:28 nan ICONN/691713353/913010049882597/200919/1100000000 nan 11000.00 8237302.11 1440
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10426540284360189
381 20-09-2019 20-09-2019 17:07:24 nan ICONN/691734386/013010100889230/2009

0.10426540284360189
788 03-10-2019 03-10-2019 10:33:28 nan ICONN/694652784/429010100082794/031019/1100000000 nan 199000.00 21133600.11 429
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10377358490566038
789 03-10-2019 03-10-2019 10:46:52 nan ICONN/694658819/910010033861989/031019/1100000000 nan 2000.00 21135600.11 006
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10476190476190476
790 03-10-2019 03-10-2019 10:48:28 nan ICONN/694659624/910010033861989/031019/1100000000 nan 2000.00 21137600.11 006
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10476190476190476
791 03-10-2019 03-10-2019 10:50:08 nan ICONN/694660427/910010033861989/031019/1100000000 nan 2000.00 21139600.11 006
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10476190476190476
792 03-10-2019 03-10-2019 10:51:26 nan ICONN/69466

0.10328638497652583
1186 14-10-2019 14-10-2019 12:32:14 nan ICONN/697345696/918010070881799/141019/1100000000 nan 10000.00 13073622.11 008
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10377358490566038
1187 14-10-2019 14-10-2019 12:35:48 nan ICONN/697347115/918010099749872/141019/1100000000 nan 5000.00 13078622.11 3763
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10377358490566038
1188 14-10-2019 14-10-2019 12:44:43 nan ICONN/697350805/912010044384224/141019/1100000000 nan 10000.00 13088622.11 783
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10377358490566038
1189 14-10-2019 14-10-2019 12:46:47 nan ICONN/697351624/914010046200250/141019/1100000000 nan 5000.00 13093622.11 067
Tran Date Value Date CHQNO Transaction Particulars  Amount(INR) DR|CR Balance(INR) Branch Name
0.10426540284360189
1190 14-10-2019 14-10-2019 12:54:47 nan ICONN

Name :- MIRAE ASSET MF COLLECTION A/C  Unnamed: 1           Unnamed: 2 Unnamed: 3                                         Unnamed: 4    Unnamed: 5    Unnamed: 6      Unnamed: 7 Unnamed: 8
0                                     Joint Holder :--          NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
1          MIRAESSET GLOBAL INVESTMENT,MAG INDIS P LTD,         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
2             UNIT-606,6TH FLR,WINDSOR OFFCST RD,KALINA         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
3                                                MUMBAI         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
4                                           MAHARASHTRA         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
5                                                400078         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
6                                           Customer No         NaN            004298598        NaN                                             Scheme           NaN     CA -CAMFS             NaN        NaN
7                                              Currency         NaN                  INR        NaN                                                NaN           NaN           NaN             NaN        NaN
8     Statement of Account No - 004010202190088 for ...         NaN                  NaN        NaN                                                NaN           NaN           NaN             NaN        NaN
9                                               Sr. No.   Tran Date            Tran Time  Cheque No                                        Particulars         Debit        Credit  Balance Amount        Sol
10                                                    1         NaN                  NaN        NaN                                    OPENING BALANCE           NaN           NaN     10390000.11        NaN
11                                                    2  15-09-2019  15-09-2019 11:58:09        NaN  ICONN/690553867/916010074330648/150919/1100000000           NaN        500.00     10390500.11       2564
12                                                    3  15-09-2019  15-09-2019 13:00:40        NaN  ICONN/690565222/018010100074078/150919/1100000000           NaN      10000.00     10400500.11        018
13                                                    4  15-09-2019  15-09-2019 13:27:58        NaN  ICONN/690569986/917010074494574/150919/1100000000           NaN      15000.00     10415500.11       1911
14                                                    5  15-09-2019  15-09-2019 21:21:12        NaN  ICONN/690644259/917010012627604/150919/1100000000           NaN       2500.00     10418000.11        022
15                                                    6  15-09-2019  15-09-2019 22:15:04        NaN  ICONN/690651462/916010024305977/150919/1100000000           NaN      10000.00     10428000.11       1914
16                                                    7  15-09-2019  15-09-2019 22:50:09        NaN  ICONN/690655420/910010035646470/150919/1100000000           NaN       3000.00     10431000.11        491
17                                                    8  15-09-2019  15-09-2019 23:13:05        NaN  ICONN/690657351/918010099112775/150919/1100000000           NaN     100000.00     10531000.11        194
18                                                    9  16-09-2019  16-09-2019 05:04:02        NaN  ICO

In [59]:
import pandas as pd

In [82]:
path = "/home/ubuntu/Downloads/sa99.xlsx"
df = pd.read_excel(path)
df['Filter'] = 'Y'
df['Filter'].where(pd.Series([True]*300), 'N')

0     Y
1     Y
2     Y
3     Y
4     Y
5     Y
6     Y
7     Y
8     Y
9     Y
10    Y
11    Y
12    Y
13    Y
14    Y
Name: Filter, dtype: object

In [64]:
pd.to_datetime(df['Transaction Date'])

ValueError: ('Unknown string format:', '31-May-19, 17:06 PM')

In [89]:
import os
import re
file_path = "/home/ubuntu/Downloads/June download statements/Axis/AXIS_Statement_004010202190088_30-06-2019.xls"
accnos = ([(re.findall('[0-9]{9,18}', str(e))) for e in os.path.basename(file_path).split("_")])
accnos = [x for x in accnos if x]
if accnos:
    if accnos[0]:
        print (accnos[0][0])

004010202190088


In [63]:
axis = "/home/ubuntu/Downloads/June download statements/Axis/axis.xls"

axis = get_new_df(pd.read_excel(axis).dropna(axis=0, how='all'), 'AXIS', 'karvy')


INFO:root:Host: 52.90.56.244
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (4.81 secs to connect)


['Sr. No.', 'Tran Date', 'Tran Time', 'Cheque No', 'Particulars', 'Debit', 'Credit', 'Balance Amount', 'Sol']


In [64]:

def axis_code_apply(row):
    if row['Filter'] == 'N':
        return row
    if str(row['Debit']) == 'nan' or (not str(row['Debit']).strip()):
        row['Created Amount'] = row['Credit']
    else:
        row['Created Amount'] = row['Debit']
    try:
#         print (row['Account Number'], str(row['Account Number']) == '004010202190088')
        if str(row['Account Number']) == '004010202190088' or str(row['Account Number']) == '4010202190088':
            row['Code'] = (str(row['Particulars']).split("/")[1])
            return row
    except:
        return row
    
    return row

In [71]:
get_new_df

<function __main__.get_new_df(df, stage, tenant_id)>

In [67]:
path = '/home/ubuntu/Downloads/issue.csv'
df = pd.read_csv(path)

In [70]:
pd.to_datetime(df['PAYMENT DATE'])

0    NaT
1    NaT
2    NaT
3    NaT
4    NaT
      ..
58   NaT
59   NaT
60   NaT
61   NaT
62   NaT
Name: PAYMENT DATE, Length: 63, dtype: datetime64[ns]

In [65]:
axis['Code'] = ''
axis['Filter'] = 'Y'
axis['Account Number'] = '004010202190088'
axis = axis.apply(axis_code_apply, axis=1)

axis

9                                               Sr. No.   Tran Date  \
10                                                    1         NaN   
11                                                    2  15-09-2019   
12                                                    3  15-09-2019   
13                                                    4  15-09-2019   
14                                                    5  15-09-2019   
...                                                 ...         ...   
1280         CLG        - \tCheque Clearing Transaction         NaN   
1281  EDC        - \tCredit transaction through EDC ...         NaN   
1282  SETU       - \tSeamless electronic fund transf...         NaN   
1283           Int.pd     - \tInterest paid to customer         NaN   
1284  Int.Coll   - \tInterest collected from the cus...         NaN   

9               Tran Time  Cheque No  \
10                    NaN        NaN   
11    15-09-2019 11:58:09        NaN   
12    15-09-2019 13:00:40        NaN   
13    15-09-2019 13:27:58        NaN   
14    15-09-2019 21:21:12        NaN   
...                   ...        ...   
1280                  NaN        NaN   
1281                  NaN        NaN   
1282                  NaN        NaN   
1283                  NaN        NaN   
1284                  NaN        NaN   

9                                           Particulars Debit    Credit  \
10                                      OPENING BALANCE   NaN       NaN   
11    ICONN/690553867/916010074330648/150919/1100000000   NaN    500.00   
12    ICONN/690565222/018010100074078/150919/1100000000   NaN  10000.00   
13    ICONN/690569986/917010074494574/150919/1100000000   NaN  15000.00   
14    ICONN/690644259/917010012627604/150919/1100000000   NaN   2500.00   
...                                                 ...   ...       ...   
1280                                                NaN   NaN       NaN   
1281                                                NaN   NaN       NaN   
1282                                                NaN   NaN       NaN   
1283                                                NaN   NaN       NaN   
1284                                                NaN   NaN       NaN   

9    Balance Amount   Sol       Code Filter   Account Number Created Amount  
10      10390000.11   NaN                 Y  004010202190088            NaN  
11      10390500.11  2564  690553867      Y  004010202190088         500.00  
12      10400500.11   018  690565222      Y  004010202190088       10000.00  
13      10415500.11  1911  690569986      Y  004010202190088       15000.00  
14      10418000.11   022  690644259      Y  004010202190088        2500.00  
...             ...   ...        ...    ...              ...            ...  
1280            NaN   NaN                 Y  004010202190088            NaN  
1281            NaN   NaN                 Y  004010202190088            NaN  
1282            NaN   NaN                 Y  004010202190088            NaN  
1283            NaN   NaN                 Y  004010202190088            NaN  
1284            NaN   NaN                 Y  004010202190088            NaN  

[1263 rows x 13 columns]

In [130]:
format_check  = "/home/ubuntu/Downloads/June download statements/SBI/SBI_Statement_00000035931670955_30-06-2019.xls"

In [169]:
from __future__ import unicode_literals
# Used to save the file as excel workbook
# Need to install this library
from xlwt import Workbook
# Used to open to corrupt excel file
import io

filename = tl99_new
# Opening the file using 'utf-16' encoding
file1 = io.open(filename, "r", encoding="utf-8")
data = file1.readlines()

# Creating a workbook object
xldoc = Workbook()
# Adding a sheet to the workbook object
sheet = xldoc.add_sheet("Sheet1", cell_overwrite_ok=True)
# Iterating and saving the data to sheet
for i, row in enumerate(data):
    # Two things are done here
    # Removeing the '\n' which comes while reading the file using io.open
    # Getting the values after splitting using '\t'
    for j, val in enumerate(row.replace('\n', '').split('\t')):
        print (i,j,val)
        sheet.write(i, j, val)
        break
# pd.read_excel(xldoc)
# Saving the file as an excel file
xldoc.save('/home/ubuntu/Downloads/myexcel_tl99.xls')

0 0 <?xml version="1.0"?>\r\n<?mso-application progid="Excel.Sheet"?>\r\n<Workbook xmlns="urn:schemas-microsoft-com:office:spreadsheet"\r\n xmlns:o="urn:schemas-microsoft-com:office:office"\r\n xmlns:x="urn:schemas-microsoft-com:office:excel"\r\n xmlns:dt="uuid:C2F41010-65B3-11d1-A29F-00AA00C14882"\r\n xmlns:ss="urn:schemas-microsoft-com:office:spreadsheet"\r\n xmlns:html="http://www.w3.org/TR/REC-html40">\r\n <DocumentProperties xmlns="urn:schemas-microsoft-com:office:office">\r\n  <Version>14.00</Version>\r\n </DocumentProperties>\r\n <CustomDocumentProperties xmlns="urn:schemas-microsoft-com:office:office">\r\n  <WorkbookGuid dt:dt="string">59274d30-69cb-4506-8a91-8b808dae9daf</WorkbookGuid>\r\n </CustomDocumentProperties>\r\n <OfficeDocumentSettings xmlns="urn:schemas-microsoft-com:office:office">\r\n  <AllowPNG/>\r\n </OfficeDocumentSettings>\r\n <ExcelWorkbook xmlns="urn:schemas-microsoft-com:office:excel">\r\n  <WindowHeight>10005</WindowHeight>\r\n  <WindowWidth>10005</WindowWi

Exception: String longer than 32767 characters

In [132]:
df = pd.read_excel('/home/ubuntu/Desktop/AlgonoxWork/oasis-main/button_functions/app/run_business_rule/myexcel_sbi.xls')

In [171]:
import pyexcel as p

with open(path, 'rb') as f:
    data = f.read()
#     print (str(data))
    data = (str(data)[14:])
    with open('/home/ubuntu/Downloads/new_tl99.xlsx', 'w') as wf:
        wf.write(data)

In [172]:
tl99_new = "/home/ubuntu/Downloads/new_tl99.xlsx"

In [176]:
os.rename(path, 'sample_file.csv')
csv = pd.read_csv("sample_file.csv", error_bad_lines=False)

FileNotFoundError: [Errno 2] No such file or directory: '/home/ubuntu/Downloads/tl99.xls' -> 'sample_file.csv'

In [188]:
path

import pandas
from bs4 import BeautifulSoup

source = 'Positions_20171110.xls'

def read_excel_xml(path):
    file = open(path).read()
    soup = BeautifulSoup(file,'xml')
    workbook = []
    for sheet in soup.findAll('Worksheet'): 
        sheet_as_list = []
        for row in sheet.findAll('Row'):
            row_as_list = []
            for cell in row.findAll('Cell'):
                row_as_list.append(cell.Data.text)
            sheet_as_list.append(row_as_list)
        workbook.append(sheet_as_list)
    return workbook


data = read_excel_xml(path)
# df = pd.DataFrame(data[0][1:],columns = data[0][0])
path

'/home/ubuntu/Downloads/tl99.xls'

In [ ]:
db_path = 

hdfc_df = hdfc_df.reset_index()
hdfc_df

In [196]:
hdfc_df = hdfc_df.reset_index()
hdfc_df

ValueError: cannot insert level_0, already exists

In [205]:
hdfc_df = pd.read_excel('')
hdfc_df = get_new_df(hdfc_df, 'CPVIRTUAL_MB99', 'karvy')

INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (6.91 secs to connect)


['Channel Partner Name', 'AMC_Code', 'Scheme Code', 'TXN ID', 'Investor Name', 'Trxn Date', 'Credit Date', 'Amount', 'Account No.', 'UTR No.']


In [207]:
hdfc_df.reset_index(drop=True)

6 Channel Partner Name AMC_Code Scheme Code   TXN ID            Investor Name    Trxn Date  Credit Date Amount     Account No.           UTR No.
0            Moneybase      MAF        EBRG  1016512  KPIO TFCBTUJBO NVLLBEBO  17-Jun-2019  17-Jun-2019   2500  00600350113104  ICIB191680006149
1            Moneybase      MAF        EBRG  1016811             Tsffkb  Objs  17-Jun-2019  17-Jun-2019   4000  00600350113104  ICIB191680006149
2            Moneybase      MAF        IORG  1016523           Qpvmptf Dibmmz  17-Jun-2019  17-Jun-2019   5000  00600350113104  ICIB191680006150
3            Moneybase      MAF        IORG  1016827             Tsffkb  Objs  17-Jun-2019  15-Jun-2019  90000  00600350113104  ICIB191660018949

In [200]:
hdfc_df['Filter'] = 'Y'
hdfc_df['Filter'] = hdfc_df['Filter'].where((hdfc_df['Debit / Credit'] == 'C'), 'N')
hdfc_df['Code'] =  hdfc_df['Reference No.']
hdfc_df

8        Transaction Date           Value Date Transaction Amount Debit / Credit               Transaction Description Reference No.       Transaction Branch Running Balance Filter          Code
9     2019-06-01 12:03:09  2019-06-01 00:00:00               3000              C     CMS-MAMFEB-190601000005/MOD/HBTRF  190601000005              KANJUR MARG        80228850      Y  190601000005
10    2019-06-01 16:35:55  2019-06-01 00:00:00               1000              C       CMS-MAMFIO-190601000012/MOD/LCT  190601000012              KANJUR MARG        80229850      Y  190601000012
11    2019-06-01 16:35:55  2019-06-01 00:00:00               2000              C       CMS-MAMFEB-190601000012/MOD/LCT  190601000012              KANJUR MARG        80231850      Y  190601000012
12    2019-06-01 16:35:55  2019-06-01 00:00:00              10000              C       CMS-MAMFPF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80241850      Y  190601000012
13    2019-06-01 16:35:55  2019-06-01 00:00:00              45000              C       CMS-MAMFTF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80286850      Y  190601000012
14    2019-06-01 16:35:55  2019-06-01 00:00:00               1000              D       CMS-MAMFIO-190601000012/MOD/LCT  190601000012              KANJUR MARG        80285850      N  190601000012
15    2019-06-01 16:35:55  2019-06-01 00:00:00               2000              D       CMS-MAMFEB-190601000012/MOD/LCT  190601000012              KANJUR MARG        80283850      N  190601000012
16    2019-06-01 16:35:55  2019-06-01 00:00:00              10000              D       CMS-MAMFPF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80273850      N  190601000012
17    2019-06-01 16:35:55  2019-06-01 00:00:00              45000              D       CMS-MAMFTF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80228850      N  190601000012
18    2019-06-01 17:20:33  2019-06-01 00:00:00               2000              C       CMS-MAMFEB-190601000013/MOD/LCT  190601000013              KANJUR MARG        80230850      Y  190601000013
19    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              C       CMS-MAMFUS-190601000013/MOD/LCT  190601000013              KANJUR MARG        80330850      Y  190601000013
20    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              C          CMS-MAMFSB-190601000013/MOD/  190601000013              KANJUR MARG        80430850      Y  190601000013
21    2019-06-01 17:20:33  2019-06-01 00:00:00             130000              C          CMS-MAMFPF-190601000013/MOD/  190601000013              KANJUR MARG        80560850      Y  190601000013
22    2019-06-01 17:20:33  2019-06-01 00:00:00             144500              C          CMS-MAMFIO-190601000013/MOD/  190601000013              KANJUR MARG        80705350      Y  190601000013
23    2019-06-01 17:20:33  2019-06-01 00:00:00             150000              C       CMS-MAMFCM-190601000013/MOD/LCT  190601000013              KANJUR MARG        80855350      Y  190601000013
24    2019-06-01 17:20:33  2019-06-01 00:00:00             252000              C          CMS-MAMFTF-190601000013/MOD/  190601000013              KANJUR MARG        81107350      Y  190601000013
25    2019-06-01 17:20:33  2019-06-01 00:00:00               2000              D       CMS-MAMFEB-190601000013/MOD/LCT  190601000013              KANJUR MARG        81105350      N  190601000013
26    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              D          CMS-MAMFSB-190601000013/MOD/  190601000013              KANJUR MARG        81005350      N  190601000013
27    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              D       CMS-MAMFUS-190601000013/MOD/LCT  190601000013              KANJUR MARG        80905350      N  190601000013
28    2019-06-01 17:20:33  2019-06-01 00:00:00             114500              D          CMS-MAMFIO

In [204]:
hdfc_df.reset_index(drop=True)

8        Transaction Date           Value Date Transaction Amount Debit / Credit               Transaction Description Reference No.       Transaction Branch Running Balance Filter          Code
0     2019-06-01 12:03:09  2019-06-01 00:00:00               3000              C     CMS-MAMFEB-190601000005/MOD/HBTRF  190601000005              KANJUR MARG        80228850      Y  190601000005
1     2019-06-01 16:35:55  2019-06-01 00:00:00               1000              C       CMS-MAMFIO-190601000012/MOD/LCT  190601000012              KANJUR MARG        80229850      Y  190601000012
2     2019-06-01 16:35:55  2019-06-01 00:00:00               2000              C       CMS-MAMFEB-190601000012/MOD/LCT  190601000012              KANJUR MARG        80231850      Y  190601000012
3     2019-06-01 16:35:55  2019-06-01 00:00:00              10000              C       CMS-MAMFPF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80241850      Y  190601000012
4     2019-06-01 16:35:55  2019-06-01 00:00:00              45000              C       CMS-MAMFTF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80286850      Y  190601000012
5     2019-06-01 16:35:55  2019-06-01 00:00:00               1000              D       CMS-MAMFIO-190601000012/MOD/LCT  190601000012              KANJUR MARG        80285850      N  190601000012
6     2019-06-01 16:35:55  2019-06-01 00:00:00               2000              D       CMS-MAMFEB-190601000012/MOD/LCT  190601000012              KANJUR MARG        80283850      N  190601000012
7     2019-06-01 16:35:55  2019-06-01 00:00:00              10000              D       CMS-MAMFPF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80273850      N  190601000012
8     2019-06-01 16:35:55  2019-06-01 00:00:00              45000              D       CMS-MAMFTF-190601000012/MOD/LCT  190601000012              KANJUR MARG        80228850      N  190601000012
9     2019-06-01 17:20:33  2019-06-01 00:00:00               2000              C       CMS-MAMFEB-190601000013/MOD/LCT  190601000013              KANJUR MARG        80230850      Y  190601000013
10    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              C       CMS-MAMFUS-190601000013/MOD/LCT  190601000013              KANJUR MARG        80330850      Y  190601000013
11    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              C          CMS-MAMFSB-190601000013/MOD/  190601000013              KANJUR MARG        80430850      Y  190601000013
12    2019-06-01 17:20:33  2019-06-01 00:00:00             130000              C          CMS-MAMFPF-190601000013/MOD/  190601000013              KANJUR MARG        80560850      Y  190601000013
13    2019-06-01 17:20:33  2019-06-01 00:00:00             144500              C          CMS-MAMFIO-190601000013/MOD/  190601000013              KANJUR MARG        80705350      Y  190601000013
14    2019-06-01 17:20:33  2019-06-01 00:00:00             150000              C       CMS-MAMFCM-190601000013/MOD/LCT  190601000013              KANJUR MARG        80855350      Y  190601000013
15    2019-06-01 17:20:33  2019-06-01 00:00:00             252000              C          CMS-MAMFTF-190601000013/MOD/  190601000013              KANJUR MARG        81107350      Y  190601000013
16    2019-06-01 17:20:33  2019-06-01 00:00:00               2000              D       CMS-MAMFEB-190601000013/MOD/LCT  190601000013              KANJUR MARG        81105350      N  190601000013
17    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              D          CMS-MAMFSB-190601000013/MOD/  190601000013              KANJUR MARG        81005350      N  190601000013
18    2019-06-01 17:20:33  2019-06-01 00:00:00             100000              D       CMS-MAMFUS-190601000013/MOD/LCT  190601000013              KANJUR MARG        80905350      N  190601000013
19    2019-06-01 17:20:33  2019-06-01 00:00:00             114500              D          CMS-MAMFIO

In [222]:
def kotak_code_apply(row):
    if row['Filter'] == 'N':
        return row
    
    if str(row['Withdrawal']) == '':
        row['Created Amount'] = row['Deposit']
    else:
        row['Created Amount'] = row['Withdrawal']
    
    try:
        
        if str(row['Account Number']) == '09582540006664':
            row['Code'] = row['Chq / Ref number'].str.split("-").index[1]
            return row
        if str(row['Account Number']) == '9312739875':
            row['Code'] = row['Description']
            return row
    except:
        return row
    
    return row

def kotak_bank(kotak_df,tenant_id):
    kotak_df['Code'] = ''   
    kotak_df['Filter'] = 'Y'
    kotak_df['Filter'] = kotak_df['Filter'].where(~kotak_df['Deposit'].isnull(), 'N')
    kotak_df['Date'] = pd.to_datetime(kotak_df['Date'],  errors='coerce')
    kotak_df['Time'] = kotak_df['Date'].dt.time
    kotak_df['Created Amount'] = ''
    kotak_df['Created Date'] = pd.to_datetime(kotak_df['Date']).dt.strftime('%Y-%m-%d')
    kotak_df = kotak_df.apply(kotak_code_apply, axis=1)
#     kotak_df = dateConvertion(kotak_df, 'KOTAK', tenant_id)

    return kotak_df
    
def syndi_bank(syndi_df, tenant_id, accno):
    syndi_df = dateConvertion(syndi_df, 'SYNDICATE', tenant_id)

    # syndi_df['Value Date'] = syndi_df['Value Date'].astype(str)
    # syndi_df['Value Date'] = pd.to_datetime(syndi_df['Value Date'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    # syndi_df['Transaction Date'] = syndi_df['Transaction Date'].astype(str)
    # syndi_df['Transaction Date'] = pd.to_datetime(syndi_df['Transaction Date'], dayfirst=True, errors='coerce').dt.strftime('%Y-%m-%d')
    account_no_fileter_map = {
            "50001010022338":["ARMY GROUP INSURAN"]
        }
    syndi_df = filter_rows(syndi_df, accno, account_no_fileter_map, 'Description')

    return syndi_df

def sbi_bank(sbi_df, tenant_id):
    sbi_df = dateConvertion(sbi_df, 'SBI', tenant_id)
    sbi_df['Value Date (HH:MM:SS)'] = pd.to_datetime(sbi_df['Value Date (HH:MM:SS)'],  errors='coerce')
    sbi_df['Time'] = sbi_df['Value Date (HH:MM:SS)'].dt.time
    sbi_df['Created Date'] = pd.to_datetime(sbi_df['Value Date (HH:MM:SS)']).dt.strftime('%Y-%m-%d')
    
    return sbi_df

In [31]:
kotak = '/home/ubuntu/Downloads/banks/kotak.xls'
sbi = '/home/ubuntu/Downloads/sbi.xlsx'
syndicate = '/home/ubuntu/Downloads/syndicate.xlsx'
axis = "/home/ubuntu/Downloads/June download statements/Axis/axis.xls"

In [33]:
axis = get_new_df(pd.read_excel(axis), 'AXIS', 'karvy')

NameError: name 'get_new_df' is not defined

In [251]:
syndicate['Filter'] = 'Y'
syndicate['Filter'].where((syndicate['Credit'].astype(str) == 'nan') , 'N')

16    Y
17    N
18    N
19    Y
20    N
21    N
22    N
23    Y
24    N
25    N
26    Y
27    Y
28    N
29    Y
30    N
31    Y
32    N
33    Y
34    N
35    Y
36    N
37    Y
38    N
39    Y
40    N
41    Y
42    N
43    N
44    Y
45    N
46    Y
47    N
48    Y
49    N
50    Y
51    N
52    Y
53    N
54    Y
55    N
56    Y
57    N
58    N
59    Y
60    N
61    Y
Name: Filter, dtype: object

In [224]:
kotak_df = get_new_df(pd.read_excel(kotak), 'KOTAK', 'karvy')

INFO:root:Host: 3.208.195.34
INFO:root:User: root
INFO:root:Password: AlgoTeam123
INFO:root:Port: 3306
INFO:root:Database: karvy_business_rules
DEBUG:root:Making connection to `karvy_business_rules`...
INFO:root:Engine created for `karvy_business_rules`
INFO:root:Connection established succesfully to `karvy_business_rules`! (20.59 secs to connect)


['Sl. No.', 'Date', 'Description', 'Chq / Ref number', 'Value Date', 'Withdrawal', 'Deposit', 'Balance', 'CR/DR']


In [226]:
kd = kotak_bank(kotak_df, 'karvy')

In [234]:
str(kd['Deposit'].iloc[0]) == 'nan'

True

In [254]:
new_tl99 = "/home/ubuntu/Downloads/tl99.xlsx"

In [255]:
pd.read_excel(new_tl99)

STP Porting Status Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4  Unnamed: 5  Unnamed: 6 Unnamed: 7 Unnamed: 8 Unnamed: 9 Unnamed: 10                  Unnamed: 11 Unnamed: 12 Unnamed: 13          Unnamed: 14            Unnamed: 15 Unnamed: 16 Unnamed: 17 Unnamed: 18      Unnamed: 19    Unnamed: 20                Unnamed: 21 Unnamed: 22 Unnamed: 23 Unnamed: 24 Unnamed: 25            Unnamed: 26 Unnamed: 27 Unnamed: 28      Unnamed: 29 Unnamed: 30 Unnamed: 31        Unnamed: 32   Unnamed: 33 Unnamed: 34 Unnamed: 35 Unnamed: 36 Unnamed: 37 Unnamed: 38 Unnamed: 39 Unnamed: 40 Unnamed: 41 Unnamed: 42 Unnamed: 43 Unnamed: 44 Unnamed: 45 Unnamed: 46 Unnamed: 47 Unnamed: 48 Unnamed: 49 Unnamed: 50 Unnamed: 51 Unnamed: 52  Unnamed: 53  Unnamed: 54 Unnamed: 55 Unnamed: 56 Unnamed: 57                Unnamed: 58 Unnamed: 59 Unnamed: 60 Unnamed: 61 Unnamed: 62 Unnamed: 63 Unnamed: 64 Unnamed: 65 Unnamed: 66 Unnamed: 67 Unnamed: 68 Unnamed: 69  \
0                               User Id : THELTD7548        NaN        NaN        NaN        NaN         NaN         NaN        NaN        NaN        NaN         NaN                          NaN         NaN         NaN                  NaN                    NaN         NaN         NaN         NaN              NaN            NaN                        NaN         NaN         NaN         NaN         NaN                    NaN         NaN         NaN              NaN         NaN         NaN                NaN           NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN          NaN          NaN         NaN         NaN         NaN                        NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN   
1                             Agent Code : ARN-82357        NaN        NaN        NaN        NaN         NaN         NaN        NaN        NaN        NaN         NaN                          NaN         NaN         NaN                  NaN                    NaN         NaN         NaN         NaN              NaN            NaN                        NaN         NaN         NaN         NaN         NaN                    NaN         NaN         NaN              NaN         NaN         NaN                NaN           NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN          NaN          NaN         NaN         NaN         NaN                        NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN   
2                     Fund : MIRAE ASSET MUTUAL FUND        NaN        NaN        NaN        NaN         NaN         NaN        NaN        NaN        NaN         NaN                          NaN         NaN         NaN                  NaN                    NaN         NaN         NaN         NaN              NaN            NaN                        NaN         NaN         NaN         NaN         NaN                    NaN         NaN         NaN              NaN         NaN         NaN                NaN           NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN          NaN          NaN         NaN         NaN         NaN                        NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN         NaN   
3                   Ported On : 6/4/2019 12:24:24 PM        NaN        NaN        NaN        NaN         NaN         N

In [100]:
df = []

with open_xlsb(format_check) as wb:
    with wb.get_sheet('Details') as sheet:
        for row in sheet.rows():
            df.append([item.v for item in row])

df = pd.DataFrame(df[1:], columns=df[0])
df

Slno      IH NO     Folio No SchemeCode                                     InvestorName  SIP Amount SIP Day  SIP Date SIP TRANS NO TRANS ID NO Batch Ref Number  Status                                             REASON Transaction ID Po No Po Amount Remittance Amount Remittance Date Remarks
0        1.0   94565764   7216840935      EBRGG                                    SBWJOEFS HJMM      2000.0      28  28052019      1199863          NA               NA  FAILED                               INSUFFICIENT BALANCE    TXMR6712498    NA        NA                NA      01/06/2019      NA
1        2.0    3926959   7016359973      EBD1G                                       SFOV TBSBG      8000.0      28  28052019     15905083          NA               NA  FAILED                               INSUFFICIENT BALANCE    TXMR6721986    NA        NA                NA      01/06/2019      NA
2        3.0    2248579   7254270324      IORGG                                    CBSLIB HBOEIJ      2000.0      28  28052019        28185          NA               NA  FAILED                               INSUFFICIENT BALANCE    TXMR6732844    NA        NA                NA      01/06/2019      NA
3        4.0  101922107   7016550925      HCRGG                               CIBSUJ C OBZHBOEIJ      5000.0      28  28052019      9062900          NA               NA  FAILED                               INSUFFICIENT BALANCE    TXMR6721380    NA        NA                NA      01/06/2019      NA
4        5.0  104934652  70115951076      TSRGG                      KBJOBSBZBO BOBOESBN TJUMBOJ      4000.0      28  28052019      2664217          NA               NA  FAILED                               INSUFFICIENT BALANCE    TXMR6743852    NA        NA                NA      01/06/2019      NA
5        6.0  104794945  70117488765      EBRGG                              QBUFM QBSFTILVNBS L      2000.0      28  28052019      2629243          NA               NA  FAILED  NOT ARRANGED FOR/AMOUNT EXCEEDING LIMIT SET BY...    TIAI2239960    NA        NA                NA      01/06/2019      NA
6        7.0  104935601  70117706245      TSRGG                                   QVTIQJUB HIPTI      4000.0      28  28052019     10553035          NA               NA    PAID                                               PAID    TXMR6734109  RTGS  12944350          12944350      01/06/2019      NA
7        8.0    4097290   7046659172      EBRGG                              EFFQ IBTNVLI HVEILB      1000.0      28  28052019     23855774          NA               NA    PAID                                               PAID    TXMR6722765  RTGS  12944350          12944350      01/06/2019      NA
8        9.0    4153050   7046744652      EBRGG                             TIBSBE WJOPE CBHBEJB      1000.0      28  28052019     24793689          NA               NA    PAID                                               PAID    TXMR6722809  RTGS  12944350          12944350      01/06/2019      NA
9       10.0   94646597   7047010642      EBRGG                                   TIPVNJM Q TIBI      3000.0      28  28052019     25232651          NA               NA    PAID                                               PAID    TXMR6722865  RTGS  12944350          12944350      01/06/2019      NA
10      11.0   94647688   7047013763      EBRGG                                  QSBCIBU KBVIBSJ      5000.0      28  28052019     25241443          NA               NA    PAID                                               PAID    TXMR6722879  RTGS  12944350          12944350      01/06/2019      NA
11      12.0   94833634   7047293292      EBRGG                      EIBSJO EIBOFTILVNBS KBZTXBM      3000.0      28  28052019     25610962          NA               NA    PAID                                               PAID    TXMR6723040  RTGS  12944350          12944350      01/06/2019      NA
12      13.0    3984446   7046469954      EBRGG                             OBNSBUB KIVOKIVOXBM

In [6]:
path = '/home/ubuntu/Downloads/tl99.xls'

In [2]:
import pandas as pd

In [7]:
# with open(path, 'r') as f:
#     print (f.read())

﻿<?xml version="1.0"?>
<?mso-application progid="Excel.Sheet"?>
<Workbook xmlns="urn:schemas-microsoft-com:office:spreadsheet"
 xmlns:o="urn:schemas-microsoft-com:office:office"
 xmlns:x="urn:schemas-microsoft-com:office:excel"
 xmlns:dt="uuid:C2F41010-65B3-11d1-A29F-00AA00C14882"
 xmlns:ss="urn:schemas-microsoft-com:office:spreadsheet"
 xmlns:html="http://www.w3.org/TR/REC-html40">
 <DocumentProperties xmlns="urn:schemas-microsoft-com:office:office">
  <LastAuthor>Suman Saurabh Lugun</LastAuthor>
  <LastSaved>2019-09-05T08:55:26Z</LastSaved>
  <Version>14.00</Version>
 </DocumentProperties>
 <CustomDocumentProperties xmlns="urn:schemas-microsoft-com:office:office">
  <WorkbookGuid dt:dt="string">54487589-0ad8-4302-bcac-e1ce44c25a8d</WorkbookGuid>
 </CustomDocumentProperties>
 <OfficeDocumentSettings xmlns="urn:schemas-microsoft-com:office:office">
  <AllowPNG/>
 </OfficeDocumentSettings>
 <ExcelWorkbook xmlns="urn:schemas-microsoft-com:office:excel">
  <WindowHeight>10005</WindowHeigh

In [4]:
import pandas as pd
import numpy as np

In [28]:
s = pd.Series(['0005t.0 ', '34444000', '355.0', np.nan])

In [30]:
s.str.replace(".0","", regex=False)


0      0005t 
1    34444000
2         355
3         NaN
dtype: object